In [7]:
from perses.utils.openeye import *
from perses.annihilation.relative import HybridTopologyFactory
from perses.rjmc.topology_proposal import PointMutationEngine
from perses.rjmc.geometry import FFAllAngleGeometryEngine

import simtk.openmm as openmm
import simtk.openmm.app as app
import simtk.unit as unit
import numpy as np
from openmoltools import forcefield_generators
import copy
import mdtraj as md
from openmmtools.constants import kB
from perses.tests.utils import validate_endstate_energies
from openforcefield.topology import Molecule
from openmmforcefields.generators import SystemGenerator

RDKit WARNING: [15:26:12] Enabling RDKit 2019.09.3 jupyter extensions


In [8]:
import os

In [9]:
ENERGY_THRESHOLD = 1e-2
temperature = 300 * unit.kelvin
kT = kB * temperature
beta = 1.0/kT

## Turn off both particle charges and exceptions charges

In [ ]:
class PointMutationExecutor(object):
    def __init__(self,
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=None,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11',
                 **kwargs):
        """
        arguments
            protein_filename : str
                path to protein (to mutate); .pdb
            mutation_chain_id : str
                name of the chain to be mutated
            mutation_residue_id : str
                residue id to change
            proposed_residue : str
                three letter code of the residue to mutate to
            phase : str, default complex
                if phase == vacuum, then the complex will not be solvated with water; else, it will be solvated with tip3p
            conduct_endstate_validation : bool, default True
                whether to conduct an endstate validation of the hybrid topology factory
            ligand_filename : str, default None
                path to ligand of interest (i.e. small molecule or protein); .sdf or .pdb
            ligand_index : int, default 0
                which ligand to use
            forcefield_files : list of str, default ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
                forcefield files for proteins and solvent
            barostat : openmm.MonteCarloBarostat, default openmm.MonteCarloBarostat(1.0 * unit.atmosphere, 300 * unit.kelvin, 50)
                barostat to use
            forcefield_kwargs : dict, default {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
                forcefield kwargs for system parametrization
            periodic_forcefield_kwargs : dict, default {'nonbondedMethod': app.PME}
                periodic forcefield kwargs for system parametrization
            nonperiodic_forcefield_kwargs : dict, default None
                non-periodic forcefield kwargs for system parametrization
            small_molecule_forcefields : str, default 'gaff-2.11'
                the forcefield string for small molecule parametrization

        TODO : allow argument for spectator ligands besides the 'ligand_filename'

        """

        # First thing to do is load the apo protein to mutate...
        protein_pdbfile = open(protein_filename, 'r')
        protein_pdb = app.PDBFile(protein_pdbfile)
        protein_pdbfile.close()
        protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
        protein_topology = protein_md_topology.to_openmm()
        protein_n_atoms = protein_md_topology.n_atoms

        # Load the ligand, if present
        molecules = []
        if ligand_filename:
            if ligand_filename.endswith('.sdf'): # small molecule
                ligand_mol = createOEMolFromSDF(ligand_filename, index=ligand_index)
                ligand_mol = generate_unique_atom_names(ligand_mol)
                molecules.append(Molecule.from_openeye(ligand_mol, allow_undefined_stereo=False))
                ligand_positions, ligand_topology = extractPositionsFromOEMol(ligand_mol),  forcefield_generators.generateTopologyFromOEMol(ligand_mol)
                ligand_md_topology = md.Topology.from_openmm(ligand_topology)
                ligand_n_atoms = ligand_md_topology.n_atoms

            elif ligand_filename.endswith('pdb'): # protein
                ligand_pdbfile = open(ligand_filename, 'r')
                ligand_pdb = app.PDBFile(ligand_pdbfile)
                ligand_pdbfile.close()
                ligand_positions, ligand_topology, ligand_md_topology = ligand_pdb.positions, ligand_pdb.topology, md.Topology.from_openmm(
                    ligand_pdb.topology)
                ligand_n_atoms = ligand_md_topology.n_atoms

            # Now create a complex
            complex_md_topology = protein_md_topology.join(ligand_md_topology)
            complex_topology = complex_md_topology.to_openmm()
            complex_positions = unit.Quantity(np.zeros([protein_n_atoms + ligand_n_atoms, 3]), unit=unit.nanometers)
            complex_positions[:protein_n_atoms, :] = protein_positions
            complex_positions[protein_n_atoms:, :] = ligand_positions

        # Now for a system_generator
        self.system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                                nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                small_molecule_forcefield=small_molecule_forcefields,
                                                molecules=molecules,
                                                cache=None)
        self.system_generator.particle_charges = False
        self.system_generator.exception_charges = False
        print(self.system_generator.particle_charges)
        print(self.system_generator.exception_charges)

        # Solvate apo and complex...
        apo_input = list(self._solvate(protein_topology, protein_positions, 'tip3p', phase=phase))
        inputs = [apo_input]
        if ligand_filename:
            inputs.append(self._solvate(complex_topology, complex_positions, 'tip3p', phase=phase))

        geometry_engine = FFAllAngleGeometryEngine(metadata=None,
                                                use_sterics=False,
                                                n_bond_divisions=100,
                                                n_angle_divisions=180,
                                                n_torsion_divisions=360,
                                                verbose=True,
                                                storage=None,
                                                bond_softening_constant=1.0,
                                                angle_softening_constant=1.0,
                                                neglect_angles = False,
                                                use_14_nonbondeds = True)


        # Run pipeline...
        htfs = []
        for (top, pos, sys) in inputs:
            point_mutation_engine = PointMutationEngine(wildtype_topology=top,
                                                                 system_generator=self.system_generator,
                                                                 chain_id=mutation_chain_id, # Denote the chain id allowed to mutate (it's always a string variable)
                                                                 max_point_mutants=1,
                                                                 residues_allowed_to_mutate=[mutation_residue_id], # The residue ids allowed to mutate
                                                                 allowed_mutations=[(mutation_residue_id, proposed_residue)], # The residue ids allowed to mutate with the three-letter code allowed to change
                                                                 aggregate=True) # Always allow aggregation

            topology_proposal = point_mutation_engine.propose(sys, top)

            new_positions, logp_proposal = geometry_engine.propose(topology_proposal, pos, beta)
            logp_reverse = geometry_engine.logp_reverse(topology_proposal, new_positions, pos, beta)
            
            top_new = md.Topology.from_openmm(topology_proposal.new_topology)
            traj = md.Trajectory(np.asarray(new_positions), top_new)
            traj.save("check_geom_new.pdb")
            
            top_old = md.Topology.from_openmm(topology_proposal.old_topology)
            traj = md.Trajectory(np.asarray(pos), top_old)
            traj.save("check_geom_old.pdb")

            forward_htf = HybridTopologyFactory(topology_proposal=topology_proposal,
                                                 current_positions=pos,
                                                 new_positions=new_positions,
                                                 use_dispersion_correction=False,
                                                 functions=None,
                                                 softcore_alpha=None,
                                                 bond_softening_constant=1.0,
                                                 angle_softening_constant=1.0,
                                                 soften_only_new=False,
                                                 neglected_new_angle_terms=[],
                                                 neglected_old_angle_terms=[],
                                                 softcore_LJ_v2=True,
                                                 softcore_electrostatics=True,
                                                 softcore_LJ_v2_alpha=0.85,
                                                 softcore_electrostatics_alpha=0.3,
                                                 softcore_sigma_Q=1.0,
                                                 interpolate_old_and_new_14s=False,
                                                 omitted_terms=None)

            if not topology_proposal.unique_new_atoms:
                assert geometry_engine.forward_final_context_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.forward_final_context_reduced_potential})"
                assert geometry_engine.forward_atoms_with_positions_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's forward atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.forward_atoms_with_positions_reduced_potential})"
                vacuum_added_valence_energy = 0.0
            else:
                added_valence_energy = geometry_engine.forward_final_context_reduced_potential - geometry_engine.forward_atoms_with_positions_reduced_potential

            if not topology_proposal.unique_old_atoms:
                assert geometry_engine.reverse_final_context_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.reverse_final_context_reduced_potential})"
                assert geometry_engine.reverse_atoms_with_positions_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.reverse_atoms_with_positions_reduced_potential})"
                subtracted_valence_energy = 0.0
            else:
                subtracted_valence_energy = geometry_engine.reverse_final_context_reduced_potential - geometry_engine.reverse_atoms_with_positions_reduced_potential


            if conduct_endstate_validation:
                zero_state_error, one_state_error = validate_endstate_energies(forward_htf._topology_proposal, forward_htf, added_valence_energy, subtracted_valence_energy, beta=beta, ENERGY_THRESHOLD=ENERGY_THRESHOLD)
                assert zero_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 0 state is above the threshold ({ENERGY_THRESHOLD}): {zero_state_error}"
                assert one_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 1 state is above the threshold ({ENERGY_THRESHOLD}): {one_state_error}"
            else:
                pass

            htfs.append(forward_htf)

        self.apo_htf = htfs[0]
        self.complex_htf = htfs[1] if ligand_filename else None

    def get_complex_htf(self):
        return self.complex_htf

    def get_apo_htf(self):
        return self.apo_htf


    def _solvate(self,
                        topology,
                        positions,
                        model,
                        phase):
        """
        Generate a solvated topology, positions, and system for a given input topology and positions.
        For generating the system, the forcefield files provided in the constructor will be used.

        Parameters
        ----------
        topology : app.Topology
            Topology of the system to solvate
        positions : [n, 3] ndarray of Quantity nm
            the positions of the unsolvated system
        forcefield : SystemGenerator.forcefield
            forcefield file of solvent to add
        model : str, default 'tip3p'
            solvent model to use for solvation

        Returns
        -------
        solvated_topology : app.Topology
            Topology of the system with added waters
        solvated_positions : [n + 3(n_waters), 3] ndarray of Quantity nm
            Solvated positions
        solvated_system : openmm.System
            The parameterized system, containing a barostat if one was specified.
        """
        modeller = app.Modeller(topology, positions)


        # Now we have to add missing atoms
        if phase != 'vacuum':
            modeller.addSolvent(self.system_generator.forcefield, model=model, padding=1.0 * unit.nanometers, ionicStrength=0.15*unit.molar)
        else:
            pass

        solvated_topology = modeller.getTopology()
        solvated_positions = modeller.getPositions()

        # Canonicalize the solvated positions: turn tuples into np.array
        solvated_positions = unit.quantity.Quantity(value=np.array([list(atom_pos) for atom_pos in solvated_positions.value_in_unit_system(unit.md_unit_system)]), unit=unit.nanometers)
        solvated_system = self.system_generator.create_system(solvated_topology)

        return solvated_topology, solvated_positions, solvated_system


In [ ]:
# Solvent
import pickle
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/4/"

# Create hybrid topology factory
apo_delivery = PointMutationExecutor(f"../input/ala_vacuum.pdb", 
                        '1', 
                        '2', 
                        'THR',
                       )
pickle.dump(apo_delivery.get_apo_htf(), open(os.path.join(output_dir, "2_0/2_0_solvent.pickle"), "wb" ))


In [ ]:
# Vacuum
import pickle
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/4/"

# Create hybrid topology factory
apo_delivery = PointMutationExecutor(f"../input/ala_vacuum.pdb", 
                              '1', 
                              '2', 
                              'THR',
                              phase='vacuum',
	                          barostat=None,
	                          periodic_forcefield_kwargs=None, 
	                          nonperiodic_forcefield_kwargs={'nonbondedMethod': app.NoCutoff}
                             )
pickle.dump(apo_delivery.get_apo_htf(), open(os.path.join(output_dir, "2_0/2_0_vacuum.pickle"), "wb" ))





## Turn off both particle charges and exceptions charges AND all LJ

In [ ]:
class PointMutationExecutor(object):
    def __init__(self,
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=None,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11',
                 **kwargs):
        """
        arguments
            protein_filename : str
                path to protein (to mutate); .pdb
            mutation_chain_id : str
                name of the chain to be mutated
            mutation_residue_id : str
                residue id to change
            proposed_residue : str
                three letter code of the residue to mutate to
            phase : str, default complex
                if phase == vacuum, then the complex will not be solvated with water; else, it will be solvated with tip3p
            conduct_endstate_validation : bool, default True
                whether to conduct an endstate validation of the hybrid topology factory
            ligand_filename : str, default None
                path to ligand of interest (i.e. small molecule or protein); .sdf or .pdb
            ligand_index : int, default 0
                which ligand to use
            forcefield_files : list of str, default ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
                forcefield files for proteins and solvent
            barostat : openmm.MonteCarloBarostat, default openmm.MonteCarloBarostat(1.0 * unit.atmosphere, 300 * unit.kelvin, 50)
                barostat to use
            forcefield_kwargs : dict, default {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
                forcefield kwargs for system parametrization
            periodic_forcefield_kwargs : dict, default {'nonbondedMethod': app.PME}
                periodic forcefield kwargs for system parametrization
            nonperiodic_forcefield_kwargs : dict, default None
                non-periodic forcefield kwargs for system parametrization
            small_molecule_forcefields : str, default 'gaff-2.11'
                the forcefield string for small molecule parametrization

        TODO : allow argument for spectator ligands besides the 'ligand_filename'

        """

        # First thing to do is load the apo protein to mutate...
        protein_pdbfile = open(protein_filename, 'r')
        protein_pdb = app.PDBFile(protein_pdbfile)
        protein_pdbfile.close()
        protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
        protein_topology = protein_md_topology.to_openmm()
        protein_n_atoms = protein_md_topology.n_atoms

        # Load the ligand, if present
        molecules = []
        if ligand_filename:
            if ligand_filename.endswith('.sdf'): # small molecule
                ligand_mol = createOEMolFromSDF(ligand_filename, index=ligand_index)
                ligand_mol = generate_unique_atom_names(ligand_mol)
                molecules.append(Molecule.from_openeye(ligand_mol, allow_undefined_stereo=False))
                ligand_positions, ligand_topology = extractPositionsFromOEMol(ligand_mol),  forcefield_generators.generateTopologyFromOEMol(ligand_mol)
                ligand_md_topology = md.Topology.from_openmm(ligand_topology)
                ligand_n_atoms = ligand_md_topology.n_atoms

            elif ligand_filename.endswith('pdb'): # protein
                ligand_pdbfile = open(ligand_filename, 'r')
                ligand_pdb = app.PDBFile(ligand_pdbfile)
                ligand_pdbfile.close()
                ligand_positions, ligand_topology, ligand_md_topology = ligand_pdb.positions, ligand_pdb.topology, md.Topology.from_openmm(
                    ligand_pdb.topology)
                ligand_n_atoms = ligand_md_topology.n_atoms

            # Now create a complex
            complex_md_topology = protein_md_topology.join(ligand_md_topology)
            complex_topology = complex_md_topology.to_openmm()
            complex_positions = unit.Quantity(np.zeros([protein_n_atoms + ligand_n_atoms, 3]), unit=unit.nanometers)
            complex_positions[:protein_n_atoms, :] = protein_positions
            complex_positions[protein_n_atoms:, :] = ligand_positions

        # Now for a system_generator
        self.system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                                nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                small_molecule_forcefield=small_molecule_forcefields,
                                                molecules=molecules,
                                                cache=None)
        self.system_generator.particle_charges = False
        self.system_generator.exception_charges = False
        self.system_generator.particle_epsilons = False
        self.system_generator.exception_epsilons = False
        print(self.system_generator.particle_charges)
        print(self.system_generator.exception_charges)
        print(self.system_generator.particle_epsilons)
        print(self.system_generator.exception_epsilons)

        # Solvate apo and complex...
        apo_input = list(self._solvate(protein_topology, protein_positions, 'tip3p', phase=phase))
        inputs = [apo_input]
        if ligand_filename:
            inputs.append(self._solvate(complex_topology, complex_positions, 'tip3p', phase=phase))

        geometry_engine = FFAllAngleGeometryEngine(metadata=None,
                                                use_sterics=False,
                                                n_bond_divisions=100,
                                                n_angle_divisions=180,
                                                n_torsion_divisions=360,
                                                verbose=True,
                                                storage=None,
                                                bond_softening_constant=1.0,
                                                angle_softening_constant=1.0,
                                                neglect_angles = False,
                                                use_14_nonbondeds = True)


        # Run pipeline...
        htfs = []
        for (top, pos, sys) in inputs:
            point_mutation_engine = PointMutationEngine(wildtype_topology=top,
                                                                 system_generator=self.system_generator,
                                                                 chain_id=mutation_chain_id, # Denote the chain id allowed to mutate (it's always a string variable)
                                                                 max_point_mutants=1,
                                                                 residues_allowed_to_mutate=[mutation_residue_id], # The residue ids allowed to mutate
                                                                 allowed_mutations=[(mutation_residue_id, proposed_residue)], # The residue ids allowed to mutate with the three-letter code allowed to change
                                                                 aggregate=True) # Always allow aggregation

            topology_proposal = point_mutation_engine.propose(sys, top)

            new_positions, logp_proposal = geometry_engine.propose(topology_proposal, pos, beta)
            logp_reverse = geometry_engine.logp_reverse(topology_proposal, new_positions, pos, beta)

            forward_htf = HybridTopologyFactory(topology_proposal=topology_proposal,
                                                 current_positions=pos,
                                                 new_positions=new_positions,
                                                 use_dispersion_correction=False,
                                                 functions=None,
                                                 softcore_alpha=None,
                                                 bond_softening_constant=1.0,
                                                 angle_softening_constant=1.0,
                                                 soften_only_new=False,
                                                 neglected_new_angle_terms=[],
                                                 neglected_old_angle_terms=[],
                                                 softcore_LJ_v2=True,
                                                 softcore_electrostatics=True,
                                                 softcore_LJ_v2_alpha=0.85,
                                                 softcore_electrostatics_alpha=0.3,
                                                 softcore_sigma_Q=1.0,
                                                 interpolate_old_and_new_14s=False,
                                                 omitted_terms=None)

            if not topology_proposal.unique_new_atoms:
                assert geometry_engine.forward_final_context_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.forward_final_context_reduced_potential})"
                assert geometry_engine.forward_atoms_with_positions_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's forward atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.forward_atoms_with_positions_reduced_potential})"
                vacuum_added_valence_energy = 0.0
            else:
                added_valence_energy = geometry_engine.forward_final_context_reduced_potential - geometry_engine.forward_atoms_with_positions_reduced_potential

            if not topology_proposal.unique_old_atoms:
                assert geometry_engine.reverse_final_context_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.reverse_final_context_reduced_potential})"
                assert geometry_engine.reverse_atoms_with_positions_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.reverse_atoms_with_positions_reduced_potential})"
                subtracted_valence_energy = 0.0
            else:
                subtracted_valence_energy = geometry_engine.reverse_final_context_reduced_potential - geometry_engine.reverse_atoms_with_positions_reduced_potential


            if conduct_endstate_validation:
                zero_state_error, one_state_error = validate_endstate_energies(forward_htf._topology_proposal, forward_htf, added_valence_energy, subtracted_valence_energy, beta=beta, ENERGY_THRESHOLD=ENERGY_THRESHOLD)
                assert zero_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 0 state is above the threshold ({ENERGY_THRESHOLD}): {zero_state_error}"
                assert one_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 1 state is above the threshold ({ENERGY_THRESHOLD}): {one_state_error}"
            else:
                pass

            htfs.append(forward_htf)

        self.apo_htf = htfs[0]
        self.complex_htf = htfs[1] if ligand_filename else None

    def get_complex_htf(self):
        return self.complex_htf

    def get_apo_htf(self):
        return self.apo_htf


    def _solvate(self,
                        topology,
                        positions,
                        model,
                        phase):
        """
        Generate a solvated topology, positions, and system for a given input topology and positions.
        For generating the system, the forcefield files provided in the constructor will be used.

        Parameters
        ----------
        topology : app.Topology
            Topology of the system to solvate
        positions : [n, 3] ndarray of Quantity nm
            the positions of the unsolvated system
        forcefield : SystemGenerator.forcefield
            forcefield file of solvent to add
        model : str, default 'tip3p'
            solvent model to use for solvation

        Returns
        -------
        solvated_topology : app.Topology
            Topology of the system with added waters
        solvated_positions : [n + 3(n_waters), 3] ndarray of Quantity nm
            Solvated positions
        solvated_system : openmm.System
            The parameterized system, containing a barostat if one was specified.
        """
        modeller = app.Modeller(topology, positions)


        # Now we have to add missing atoms
        if phase != 'vacuum':
            modeller.addSolvent(self.system_generator.forcefield, model=model, padding=1.0 * unit.nanometers, ionicStrength=0.15*unit.molar)
        else:
            pass

        solvated_topology = modeller.getTopology()
        solvated_positions = modeller.getPositions()

        # Canonicalize the solvated positions: turn tuples into np.array
        solvated_positions = unit.quantity.Quantity(value=np.array([list(atom_pos) for atom_pos in solvated_positions.value_in_unit_system(unit.md_unit_system)]), unit=unit.nanometers)
        solvated_system = self.system_generator.create_system(solvated_topology)

        return solvated_topology, solvated_positions, solvated_system


In [ ]:
# Solvent
import pickle
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/4/"

# Create hybrid topology factory
apo_delivery = PointMutationExecutor(f"../input/ala_vacuum.pdb", 
                        '1', 
                        '2', 
                        'THR',
                       )
pickle.dump(apo_delivery.get_apo_htf(), open(os.path.join(output_dir, "2_0/2_0_solvent.pickle"), "wb" ))


In [ ]:
# Vacuum
import pickle
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/4/"

# Create hybrid topology factory
apo_delivery = PointMutationExecutor(f"../input/ala_vacuum.pdb", 
                              '1', 
                              '2', 
                              'THR',
                              phase='vacuum',
	                          barostat=None,
	                          periodic_forcefield_kwargs=None, 
	                          nonperiodic_forcefield_kwargs={'nonbondedMethod': app.NoCutoff}
                             )
pickle.dump(apo_delivery.get_apo_htf(), open(os.path.join(output_dir, "2_0/2_0_vacuum.pickle"), "wb" ))





## run fully interacting system at lambda = 1

In [4]:
import logging
import pickle
import numpy as np
from openmmtools.integrators import PeriodicNonequilibriumIntegrator
from simtk import unit
from simtk import openmm
import argparse
import os
import time
from simtk.openmm.app import PDBFile
import mdtraj as md

In [5]:
# Set up logger
_logger = logging.getLogger()
_logger.setLevel(logging.DEBUG)


In [6]:
# Define lambda functions
x = 'lambda'
DEFAULT_ALCHEMICAL_FUNCTIONS = {
                             'lambda_sterics_core': x,
                             'lambda_electrostatics_core': x,
                             'lambda_sterics_insert': f"select(step({x} - 0.5), 1.0, 2.0 * {x})",
                             'lambda_sterics_delete': f"select(step({x} - 0.5), 2.0 * ({x} - 0.5), 0.0)",
                             'lambda_electrostatics_insert': f"select(step({x} - 0.5), 2.0 * ({x} - 0.5), 0.0)",
                             'lambda_electrostatics_delete': f"select(step({x} - 0.5), 1.0, 2.0 * {x})",
                             'lambda_bonds': x,
                             'lambda_angles': x,
                             'lambda_torsions': x}

In [7]:
# Define simulation parameters
nsteps_eq = 62500 # 0.25 ns
nsteps_neq = 20000 # 80 ps
neq_splitting ='V R H O R V'
timestep = 4.0 * unit.femtosecond
platform_name = 'CUDA'


In [8]:
# Read in htf
with open("/data/chodera/zhangi/perses_benchmark/neq/3/2/2_solvent.pickle", 'rb') as f:
    htf = pickle.load(f)
system = htf.hybrid_system
positions = htf.hybrid_positions

In [4]:
import openmmtools
from simtk.unit import *
# Set up integrator
integrator = PeriodicNonequilibriumIntegrator(DEFAULT_ALCHEMICAL_FUNCTIONS, nsteps_eq, nsteps_neq, neq_splitting, timestep=timestep)

# Set up context
platform = openmm.Platform.getPlatformByName(platform_name)
if platform_name in ['CUDA', 'OpenCL']:
    platform.setPropertyDefaultValue('Precision', 'mixed')
if platform_name in ['CUDA']:
    platform.setPropertyDefaultValue('DeterministicForces', 'true')
context = openmm.Context(system, integrator, platform)
context.setPeriodicBoxVectors(*system.getDefaultPeriodicBoxVectors())
context.setPositions(positions)



NameError: name 'DEFAULT_ALCHEMICAL_FUNCTIONS' is not defined

In [ ]:
# Set up context
platform = openmm.Platform.getPlatformByName(platform_name)
if platform_name in ['CUDA', 'OpenCL']:
    platform.setPropertyDefaultValue('Precision', 'mixed')
if platform_name in ['CUDA']:
    platform.setPropertyDefaultValue('DeterministicForces', 'true')
context = openmm.Context(system, integrator, platform)
context.setPeriodicBoxVectors(*system.getDefaultPeriodicBoxVectors())
context.setPositions(positions)


In [17]:
swig_parameters = context.getParameters()
context_parameters = {q: swig_parameters[q] for q in swig_parameters}

In [18]:
context.setParameter('lambda_angles', 1)
context.setParameter('lambda_bonds', 1)
context.setParameter('lambda_electrostatics_core', 1)
context.setParameter('lambda_electrostatics_delete', 1)
context.setParameter('lambda_electrostatics_insert', 1)
context.setParameter('lambda_sterics_core', 1)
context.setParameter('lambda_sterics_delete', 1)
context.setParameter('lambda_sterics_insert', 1)
context.setParameter('lambda_torsions', 1)

In [19]:
swig_parameters = context.getParameters()
context_parameters = {q: swig_parameters[q] for q in swig_parameters}
context_parameters

{'MonteCarloPressure': 1.01325,
 'MonteCarloTemperature': 300.0,
 'lambda_angles': 1.0,
 'lambda_bonds': 1.0,
 'lambda_electrostatics_core': 1.0,
 'lambda_electrostatics_delete': 1.0,
 'lambda_electrostatics_insert': 1.0,
 'lambda_sterics_core': 1.0,
 'lambda_sterics_delete': 1.0,
 'lambda_sterics_insert': 1.0,
 'lambda_torsions': 1.0,
 'softcore_alpha': 0.85}

In [20]:
# Minimize
openmm.LocalEnergyMinimizer.minimize(context)

# Run equilibration
traj = list()
for step in range(nsteps_eq):
    if step % 750 == 0:
        traj = traj[-10:]
    pos = context.getState(getPositions=True, enforcePeriodicBox=False).getPositions(asNumpy=True)
    new_pos = np.asarray(htf.new_positions(pos))
    traj.append(new_pos)
    initial_time = time.time()
    integrator.step(1)
    elapsed_time = (time.time() - initial_time) * seconds
    _logger.info(f'Step: {step} took {elapsed_time} seconds')


INFO:root:Step: 0 took 0.404803991317749 s seconds
INFO:root:Step: 1 took 0.0031957626342773438 s seconds
INFO:root:Step: 2 took 0.0029468536376953125 s seconds
INFO:root:Step: 3 took 0.002553224563598633 s seconds
INFO:root:Step: 4 took 0.0025064945220947266 s seconds
INFO:root:Step: 5 took 0.0027341842651367188 s seconds
INFO:root:Step: 6 took 0.0025093555450439453 s seconds
INFO:root:Step: 7 took 0.002653360366821289 s seconds
INFO:root:Step: 8 took 0.002458810806274414 s seconds
INFO:root:Step: 9 took 0.0026063919067382812 s seconds
INFO:root:Step: 10 took 0.0026903152465820312 s seconds
INFO:root:Step: 11 took 0.002696990966796875 s seconds
INFO:root:Step: 12 took 0.0026259422302246094 s seconds
INFO:root:Step: 13 took 0.0026111602783203125 s seconds
INFO:root:Step: 14 took 0.002516031265258789 s seconds
INFO:root:Step: 15 took 0.0028045177459716797 s seconds
INFO:root:Step: 16 took 0.0026311874389648438 s seconds
INFO:root:Step: 17 took 0.002496480941772461 s seconds
INFO:root:St

INFO:root:Step: 148 took 0.0027587413787841797 s seconds
INFO:root:Step: 149 took 0.0038328170776367188 s seconds
INFO:root:Step: 150 took 0.0026917457580566406 s seconds
INFO:root:Step: 151 took 0.0026717185974121094 s seconds
INFO:root:Step: 152 took 0.002670764923095703 s seconds
INFO:root:Step: 153 took 0.0027132034301757812 s seconds
INFO:root:Step: 154 took 0.002821683883666992 s seconds
INFO:root:Step: 155 took 0.0028984546661376953 s seconds
INFO:root:Step: 156 took 0.002725362777709961 s seconds
INFO:root:Step: 157 took 0.0027875900268554688 s seconds
INFO:root:Step: 158 took 0.002758502960205078 s seconds
INFO:root:Step: 159 took 0.0027616024017333984 s seconds
INFO:root:Step: 160 took 0.002847433090209961 s seconds
INFO:root:Step: 161 took 0.0027785301208496094 s seconds
INFO:root:Step: 162 took 0.002566099166870117 s seconds
INFO:root:Step: 163 took 0.0027403831481933594 s seconds
INFO:root:Step: 164 took 0.0027298927307128906 s seconds
INFO:root:Step: 165 took 0.0027635097

INFO:root:Step: 293 took 0.002877473831176758 s seconds
INFO:root:Step: 294 took 0.0027191638946533203 s seconds
INFO:root:Step: 295 took 0.002736330032348633 s seconds
INFO:root:Step: 296 took 0.0028340816497802734 s seconds
INFO:root:Step: 297 took 0.0028448104858398438 s seconds
INFO:root:Step: 298 took 0.0028181076049804688 s seconds
INFO:root:Step: 299 took 0.003920316696166992 s seconds
INFO:root:Step: 300 took 0.003147602081298828 s seconds
INFO:root:Step: 301 took 0.00266265869140625 s seconds
INFO:root:Step: 302 took 0.002836465835571289 s seconds
INFO:root:Step: 303 took 0.002620697021484375 s seconds
INFO:root:Step: 304 took 0.0028078556060791016 s seconds
INFO:root:Step: 305 took 0.002753019332885742 s seconds
INFO:root:Step: 306 took 0.0028350353240966797 s seconds
INFO:root:Step: 307 took 0.0027923583984375 s seconds
INFO:root:Step: 308 took 0.0029408931732177734 s seconds
INFO:root:Step: 309 took 0.0028607845306396484 s seconds
INFO:root:Step: 310 took 0.0026853084564208

INFO:root:Step: 439 took 0.0028963088989257812 s seconds
INFO:root:Step: 440 took 0.0028607845306396484 s seconds
INFO:root:Step: 441 took 0.0028603076934814453 s seconds
INFO:root:Step: 442 took 0.0027060508728027344 s seconds
INFO:root:Step: 443 took 0.00273895263671875 s seconds
INFO:root:Step: 444 took 0.002752542495727539 s seconds
INFO:root:Step: 445 took 0.003312826156616211 s seconds
INFO:root:Step: 446 took 0.002691984176635742 s seconds
INFO:root:Step: 447 took 0.0029022693634033203 s seconds
INFO:root:Step: 448 took 0.0027856826782226562 s seconds
INFO:root:Step: 449 took 0.004002809524536133 s seconds
INFO:root:Step: 450 took 0.002887725830078125 s seconds
INFO:root:Step: 451 took 0.007813215255737305 s seconds
INFO:root:Step: 452 took 0.0028548240661621094 s seconds
INFO:root:Step: 453 took 0.0029218196868896484 s seconds
INFO:root:Step: 454 took 0.0033674240112304688 s seconds
INFO:root:Step: 455 took 0.0030744075775146484 s seconds
INFO:root:Step: 456 took 0.002720832824

INFO:root:Step: 585 took 0.0027718544006347656 s seconds
INFO:root:Step: 586 took 0.0028679370880126953 s seconds
INFO:root:Step: 587 took 0.0027146339416503906 s seconds
INFO:root:Step: 588 took 0.002786397933959961 s seconds
INFO:root:Step: 589 took 0.0027899742126464844 s seconds
INFO:root:Step: 590 took 0.002902507781982422 s seconds
INFO:root:Step: 591 took 0.0028684139251708984 s seconds
INFO:root:Step: 592 took 0.0027844905853271484 s seconds
INFO:root:Step: 593 took 0.002774953842163086 s seconds
INFO:root:Step: 594 took 0.0029854774475097656 s seconds
INFO:root:Step: 595 took 0.002781391143798828 s seconds
INFO:root:Step: 596 took 0.002777099609375 s seconds
INFO:root:Step: 597 took 0.0027379989624023438 s seconds
INFO:root:Step: 598 took 0.0028200149536132812 s seconds
INFO:root:Step: 599 took 0.004011392593383789 s seconds
INFO:root:Step: 600 took 0.0029125213623046875 s seconds
INFO:root:Step: 601 took 0.002704620361328125 s seconds
INFO:root:Step: 602 took 0.00279927253723

...

INFO:root:Step: 61799 took 0.004237174987792969 s seconds
INFO:root:Step: 61800 took 0.002947568893432617 s seconds
INFO:root:Step: 61801 took 0.003093719482421875 s seconds
INFO:root:Step: 61802 took 0.0031244754791259766 s seconds
INFO:root:Step: 61803 took 0.003030061721801758 s seconds
INFO:root:Step: 61804 took 0.003123044967651367 s seconds
INFO:root:Step: 61805 took 0.0031070709228515625 s seconds
INFO:root:Step: 61806 took 0.0030930042266845703 s seconds
INFO:root:Step: 61807 took 0.0034170150756835938 s seconds
INFO:root:Step: 61808 took 0.003228902816772461 s seconds
INFO:root:Step: 61809 took 0.0029811859130859375 s seconds
INFO:root:Step: 61810 took 0.0031592845916748047 s seconds
INFO:root:Step: 61811 took 0.003213167190551758 s seconds
INFO:root:Step: 61812 took 0.0031113624572753906 s seconds
INFO:root:Step: 61813 took 0.00307464599609375 s seconds
INFO:root:Step: 61814 took 0.0030853748321533203 s seconds
INFO:root:Step: 61815 took 0.0029783248901367188 s seconds
INFO:r

INFO:root:Step: 61939 took 0.0032236576080322266 s seconds
INFO:root:Step: 61940 took 0.0031032562255859375 s seconds
INFO:root:Step: 61941 took 0.0033180713653564453 s seconds
INFO:root:Step: 61942 took 0.003087759017944336 s seconds
INFO:root:Step: 61943 took 0.0029494762420654297 s seconds
INFO:root:Step: 61944 took 0.0030040740966796875 s seconds
INFO:root:Step: 61945 took 0.003147125244140625 s seconds
INFO:root:Step: 61946 took 0.003267049789428711 s seconds
INFO:root:Step: 61947 took 0.0031685829162597656 s seconds
INFO:root:Step: 61948 took 0.003177165985107422 s seconds
INFO:root:Step: 61949 took 0.004794120788574219 s seconds
INFO:root:Step: 61950 took 0.0033202171325683594 s seconds
INFO:root:Step: 61951 took 0.003229379653930664 s seconds
INFO:root:Step: 61952 took 0.0030906200408935547 s seconds
INFO:root:Step: 61953 took 0.0030264854431152344 s seconds
INFO:root:Step: 61954 took 0.0033588409423828125 s seconds
INFO:root:Step: 61955 took 0.003059864044189453 s seconds
INFO

INFO:root:Step: 62079 took 0.0030450820922851562 s seconds
INFO:root:Step: 62080 took 0.0030672550201416016 s seconds
INFO:root:Step: 62081 took 0.0030908584594726562 s seconds
INFO:root:Step: 62082 took 0.0032563209533691406 s seconds
INFO:root:Step: 62083 took 0.00304412841796875 s seconds
INFO:root:Step: 62084 took 0.0029942989349365234 s seconds
INFO:root:Step: 62085 took 0.0032215118408203125 s seconds
INFO:root:Step: 62086 took 0.0031585693359375 s seconds
INFO:root:Step: 62087 took 0.0031740665435791016 s seconds
INFO:root:Step: 62088 took 0.0029828548431396484 s seconds
INFO:root:Step: 62089 took 0.003101348876953125 s seconds
INFO:root:Step: 62090 took 0.003049135208129883 s seconds
INFO:root:Step: 62091 took 0.0030243396759033203 s seconds
INFO:root:Step: 62092 took 0.0030901432037353516 s seconds
INFO:root:Step: 62093 took 0.0030841827392578125 s seconds
INFO:root:Step: 62094 took 0.002888917922973633 s seconds
INFO:root:Step: 62095 took 0.0029859542846679688 s seconds
INFO:

INFO:root:Step: 62220 took 0.0031082630157470703 s seconds
INFO:root:Step: 62221 took 0.0031206607818603516 s seconds
INFO:root:Step: 62222 took 0.0033686161041259766 s seconds
INFO:root:Step: 62223 took 0.0031137466430664062 s seconds
INFO:root:Step: 62224 took 0.0033385753631591797 s seconds
INFO:root:Step: 62225 took 0.003226041793823242 s seconds
INFO:root:Step: 62226 took 0.0031099319458007812 s seconds
INFO:root:Step: 62227 took 0.0031871795654296875 s seconds
INFO:root:Step: 62228 took 0.0032532215118408203 s seconds
INFO:root:Step: 62229 took 0.0030291080474853516 s seconds
INFO:root:Step: 62230 took 0.002912282943725586 s seconds
INFO:root:Step: 62231 took 0.002955198287963867 s seconds
INFO:root:Step: 62232 took 0.0030536651611328125 s seconds
INFO:root:Step: 62233 took 0.003305673599243164 s seconds
INFO:root:Step: 62234 took 0.003036022186279297 s seconds
INFO:root:Step: 62235 took 0.0033004283905029297 s seconds
INFO:root:Step: 62236 took 0.0030829906463623047 s seconds
IN

INFO:root:Step: 62360 took 0.003109455108642578 s seconds
INFO:root:Step: 62361 took 0.0030345916748046875 s seconds
INFO:root:Step: 62362 took 0.0030291080474853516 s seconds
INFO:root:Step: 62363 took 0.0032324790954589844 s seconds
INFO:root:Step: 62364 took 0.0030634403228759766 s seconds
INFO:root:Step: 62365 took 0.0031747817993164062 s seconds
INFO:root:Step: 62366 took 0.0029647350311279297 s seconds
INFO:root:Step: 62367 took 0.0029325485229492188 s seconds
INFO:root:Step: 62368 took 0.0030868053436279297 s seconds
INFO:root:Step: 62369 took 0.0032126903533935547 s seconds
INFO:root:Step: 62370 took 0.003203868865966797 s seconds
INFO:root:Step: 62371 took 0.0030889511108398438 s seconds
INFO:root:Step: 62372 took 0.0031774044036865234 s seconds
INFO:root:Step: 62373 took 0.0033044815063476562 s seconds
INFO:root:Step: 62374 took 0.003197908401489258 s seconds
INFO:root:Step: 62375 took 0.0031447410583496094 s seconds
INFO:root:Step: 62376 took 0.003208160400390625 s seconds
I

AttributeError: 'list' object has no attribute 'shape'

In [21]:
import mdtraj as md
top_new = md.Topology.from_openmm(htf._topology_proposal.new_topology)
traj = md.Trajectory(np.array(traj), top_new)
traj.save("ala_ser.pdb")

## Run full free energy calc and check atoms that nan

In [2]:
import os
import numpy as np
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_solvent_forward_neq_old_pos.npy", 'rb') as f:
    fwd_old_pos = np.load(f)

In [3]:
fwd_old_pos.shape

(205, 1988, 3)

In [4]:
import math
for i, atom in enumerate(fwd_old_pos[121]):
    if math.isnan(atom[0]) or math.isnan(atom[1]) or math.isnan(atom[2]):
        print(i, atom)

10 [nan nan nan]
11 [nan nan nan]
12 [nan nan nan]
15 [nan nan nan]


In [5]:
import os
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_solvent_forward_neq_new_pos.npy", 'rb') as f:
    fwd_new_pos = np.load(f)

In [6]:
fwd_new_pos.shape

(205, 1992, 3)

In [11]:
import math
for i, atom in enumerate(fwd_new_pos[121]):
    if math.isnan(atom[0]) or math.isnan(atom[1]) or math.isnan(atom[2]):
        print(i, atom)

10 [nan nan nan]
13 [nan nan nan]


In [8]:
import math
for i, atom in enumerate(fwd_old_pos[121]):
    if math.isnan(atom[0]) or math.isnan(atom[1]) or math.isnan(atom[2]):
        print(i, atom)

10 [nan nan nan]
11 [nan nan nan]
12 [nan nan nan]
15 [nan nan nan]


In [10]:
import os
import numpy as np
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_vacuum_forward_equil_pos.npy", 'rb') as f:
    fwd_old_pos = np.load(f)

In [11]:
fwd_old_pos.shape

(260, 22, 3)

In [15]:
import math
for i, atom in enumerate(fwd_old_pos[0]):
    if math.isnan(atom[0]) or math.isnan(atom[1]) or math.isnan(atom[2]):
        print(i, atom)

0 [nan nan nan]
1 [nan nan nan]
2 [nan nan nan]
3 [nan nan nan]
10 [nan nan nan]
11 [nan nan nan]
12 [nan nan nan]
15 [nan nan nan]
18 [nan nan nan]
19 [nan nan nan]
20 [nan nan nan]
21 [nan nan nan]


In [8]:
# Read in htf
import pickle
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_solvent.pickle", 'rb') as f:
    htf = pickle.load(f)

In [73]:
for atom in htf._topology_proposal.old_topology.atoms():
    print(atom)

<Atom 0 (H1) of chain 0 residue 0 (ACE)>
<Atom 1 (CH3) of chain 0 residue 0 (ACE)>
<Atom 2 (H2) of chain 0 residue 0 (ACE)>
<Atom 3 (H3) of chain 0 residue 0 (ACE)>
<Atom 4 (C) of chain 0 residue 0 (ACE)>
<Atom 5 (O) of chain 0 residue 0 (ACE)>
<Atom 6 (N) of chain 0 residue 1 (ALA)>
<Atom 7 (H) of chain 0 residue 1 (ALA)>
<Atom 8 (CA) of chain 0 residue 1 (ALA)>
<Atom 9 (HA) of chain 0 residue 1 (ALA)>
<Atom 10 (CB) of chain 0 residue 1 (ALA)>
<Atom 11 (HB2) of chain 0 residue 1 (ALA)>
<Atom 12 (HB3) of chain 0 residue 1 (ALA)>
<Atom 13 (C) of chain 0 residue 1 (ALA)>
<Atom 14 (O) of chain 0 residue 1 (ALA)>
<Atom 15 (HB1) of chain 0 residue 1 (ALA)>
<Atom 16 (N) of chain 0 residue 2 (NME)>
<Atom 17 (H) of chain 0 residue 2 (NME)>
<Atom 18 (C) of chain 0 residue 2 (NME)>
<Atom 19 (H1) of chain 0 residue 2 (NME)>
<Atom 20 (H2) of chain 0 residue 2 (NME)>
<Atom 21 (H3) of chain 0 residue 2 (NME)>
<Atom 22 (O) of chain 1 residue 3 (HOH)>
<Atom 23 (H1) of chain 1 residue 3 (HOH)>
<Atom 24

<Atom 1789 (O) of chain 1 residue 592 (HOH)>
<Atom 1790 (H1) of chain 1 residue 592 (HOH)>
<Atom 1791 (H2) of chain 1 residue 592 (HOH)>
<Atom 1792 (O) of chain 1 residue 593 (HOH)>
<Atom 1793 (H1) of chain 1 residue 593 (HOH)>
<Atom 1794 (H2) of chain 1 residue 593 (HOH)>
<Atom 1795 (O) of chain 1 residue 594 (HOH)>
<Atom 1796 (H1) of chain 1 residue 594 (HOH)>
<Atom 1797 (H2) of chain 1 residue 594 (HOH)>
<Atom 1798 (O) of chain 1 residue 595 (HOH)>
<Atom 1799 (H1) of chain 1 residue 595 (HOH)>
<Atom 1800 (H2) of chain 1 residue 595 (HOH)>
<Atom 1801 (O) of chain 1 residue 596 (HOH)>
<Atom 1802 (H1) of chain 1 residue 596 (HOH)>
<Atom 1803 (H2) of chain 1 residue 596 (HOH)>
<Atom 1804 (O) of chain 1 residue 597 (HOH)>
<Atom 1805 (H1) of chain 1 residue 597 (HOH)>
<Atom 1806 (H2) of chain 1 residue 597 (HOH)>
<Atom 1807 (O) of chain 1 residue 598 (HOH)>
<Atom 1808 (H1) of chain 1 residue 598 (HOH)>
<Atom 1809 (H2) of chain 1 residue 598 (HOH)>
<Atom 1810 (O) of chain 1 residue 599 (HO

In [74]:
for atom in htf._topology_proposal.new_topology.atoms():
    print(atom)

<Atom 0 (H1) of chain 0 residue 0 (ACE)>
<Atom 1 (CH3) of chain 0 residue 0 (ACE)>
<Atom 2 (H2) of chain 0 residue 0 (ACE)>
<Atom 3 (H3) of chain 0 residue 0 (ACE)>
<Atom 4 (C) of chain 0 residue 0 (ACE)>
<Atom 5 (O) of chain 0 residue 0 (ACE)>
<Atom 6 (N) of chain 0 residue 1 (THR)>
<Atom 7 (H) of chain 0 residue 1 (THR)>
<Atom 8 (CA) of chain 0 residue 1 (THR)>
<Atom 9 (HA) of chain 0 residue 1 (THR)>
<Atom 10 (CB) of chain 0 residue 1 (THR)>
<Atom 11 (C) of chain 0 residue 1 (THR)>
<Atom 12 (O) of chain 0 residue 1 (THR)>
<Atom 13 (HB) of chain 0 residue 1 (THR)>
<Atom 14 (CG2) of chain 0 residue 1 (THR)>
<Atom 15 (HG21) of chain 0 residue 1 (THR)>
<Atom 16 (HG22) of chain 0 residue 1 (THR)>
<Atom 17 (HG23) of chain 0 residue 1 (THR)>
<Atom 18 (OG1) of chain 0 residue 1 (THR)>
<Atom 19 (HG1) of chain 0 residue 1 (THR)>
<Atom 20 (N) of chain 0 residue 2 (NME)>
<Atom 21 (H) of chain 0 residue 2 (NME)>
<Atom 22 (C) of chain 0 residue 2 (NME)>
<Atom 23 (H1) of chain 0 residue 2 (NME)>
<

<Atom 1837 (H2) of chain 1 residue 606 (HOH)>
<Atom 1838 (O) of chain 1 residue 607 (HOH)>
<Atom 1839 (H1) of chain 1 residue 607 (HOH)>
<Atom 1840 (H2) of chain 1 residue 607 (HOH)>
<Atom 1841 (O) of chain 1 residue 608 (HOH)>
<Atom 1842 (H1) of chain 1 residue 608 (HOH)>
<Atom 1843 (H2) of chain 1 residue 608 (HOH)>
<Atom 1844 (O) of chain 1 residue 609 (HOH)>
<Atom 1845 (H1) of chain 1 residue 609 (HOH)>
<Atom 1846 (H2) of chain 1 residue 609 (HOH)>
<Atom 1847 (O) of chain 1 residue 610 (HOH)>
<Atom 1848 (H1) of chain 1 residue 610 (HOH)>
<Atom 1849 (H2) of chain 1 residue 610 (HOH)>
<Atom 1850 (O) of chain 1 residue 611 (HOH)>
<Atom 1851 (H1) of chain 1 residue 611 (HOH)>
<Atom 1852 (H2) of chain 1 residue 611 (HOH)>
<Atom 1853 (O) of chain 1 residue 612 (HOH)>
<Atom 1854 (H1) of chain 1 residue 612 (HOH)>
<Atom 1855 (H2) of chain 1 residue 612 (HOH)>
<Atom 1856 (O) of chain 1 residue 613 (HOH)>
<Atom 1857 (H1) of chain 1 residue 613 (HOH)>
<Atom 1858 (H2) of chain 1 residue 613 (H

In [9]:
# Save new pos to pdb
import mdtraj as md
top_new = md.Topology.from_openmm(htf._topology_proposal.new_topology)
traj = md.Trajectory(np.array(fwd_new_pos[:121]), top_new)
traj.save("ala_thr_new.pdb")

In [10]:
# Save new pos to pdb
import mdtraj as md
top_old = md.Topology.from_openmm(htf._topology_proposal.old_topology)
traj = md.Trajectory(np.array(fwd_old_pos[:121]), top_old)
traj.save("ala_thr_old.pdb")

#### Check that vacuum positions do not contain nans

In [5]:
import os
import numpy as np


In [8]:
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_vacuum_forward_neq_old_pos.npy", 'rb') as f:
    fwd_old_pos = np.load(f)

In [9]:
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_vacuum_forward_neq_new_pos.npy", 'rb') as f:
    fwd_new_pos = np.load(f)

In [6]:
with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_vacuum_reverse_neq_old_pos.npy", 'rb') as f:
    rev_old_pos = np.load(f)

In [2]:

with open("/data/chodera/zhangi/perses_benchmark/neq/4/2_1/2_1_vacuum_reverse_neq_new_pos.npy", 'rb') as f:
    rev_new_pos = np.load(f)

In [11]:
for pos in fwd_new_pos:
    print(pos)

[[            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.18847375e+09 -5.67790821e+08 -3.16111167e+08]
 [-3.64752623e+08  7.94919278e+07 -7.80617321e+08]
 [ 5.50541522e+09  4.69323985e+09 -4.09084889e+09]
 [ 5.50541522e+09  4.69323985e+09 -4.09084889e+09]
 [-2.24726248e+09 -1.55604180e+09 -4.74619874e+09]
 [-2.24726248e+09 -1.55604181e+09 -4.74619874e+09]
 [            nan             nan             nan]
 [ 9.46986045e+08  9.07063234e+08 -3.47130554e+09]
 [ 1.62426936e+09  1.42482442e+09 -3.20127383e+09]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.71718426e+07 -2.32324584e+07 -2.42424843e+07]
 [-1.71718426e+07 -2.32324583e+

[[            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.18817595e+09 -5.67993806e+08 -3.15912847e+08]
 [-3.64248335e+08  7.96918198e+07 -7.80624533e+08]
 [ 5.50494204e+09  4.69280543e+09 -4.09128381e+09]
 [ 5.50494204e+09  4.69280543e+09 -4.09128381e+09]
 [-2.26933704e+09 -1.55910758e+09 -4.74658724e+09]
 [-2.26933704e+09 -1.55910758e+09 -4.74658724e+09]
 [            nan             nan             nan]
 [ 9.45997638e+08  9.09659837e+08 -3.46843152e+09]
 [ 1.61931309e+09  1.42528265e+09 -3.20138539e+09]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.71718426e+07 -2.32324585e+07 -2.42424844e+07]
 [-1.71718426e+07 -2.32324586e+

[[            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.18804951e+09 -5.68079990e+08 -3.15828644e+08]
 [-3.64994275e+08  7.88453379e+07 -7.80079667e+08]
 [ 5.50474114e+09  4.69262098e+09 -4.09146847e+09]
 [ 5.50474114e+09  4.69262098e+09 -4.09146847e+09]
 [-2.26528867e+09 -1.56116856e+09 -4.76012778e+09]
 [-2.26528867e+09 -1.56116856e+09 -4.76012778e+09]
 [            nan             nan             nan]
 [ 9.46609602e+08  9.06621626e+08 -3.46713943e+09]
 [ 1.61659100e+09  1.42655067e+09 -3.20129769e+09]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.71718428e+07 -2.32324587e+07 -2.42424844e+07]
 [-1.71718428e+07 -2.32324587e+

 [            nan             nan             nan]]
[[            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.18797778e+09 -5.68128877e+08 -3.15780881e+08]
 [-3.66256425e+08  7.77916587e+07 -7.79422366e+08]
 [ 5.50462718e+09  4.69251635e+09 -4.09157322e+09]
 [ 5.50462718e+09  4.69251635e+09 -4.09157322e+09]
 [-2.26049499e+09 -1.56447862e+09 -4.76421437e+09]
 [-2.26049499e+09 -1.56447862e+09 -4.76421437e+09]
 [            nan             nan             nan]
 [ 9.47173035e+08  9.04237577e+08 -3.46787653e+09]
 [ 1.61760611e+09  1.41991702e+09 -3.20009400e+09]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [            nan             nan             nan]
 [-1.71718430e+07 -2.32324588e

## Edit map

In [12]:
class PointMutationExecutor(object):
    def __init__(self,
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=None,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11',
                 **kwargs):
        """
        arguments
            protein_filename : str
                path to protein (to mutate); .pdb
            mutation_chain_id : str
                name of the chain to be mutated
            mutation_residue_id : str
                residue id to change
            proposed_residue : str
                three letter code of the residue to mutate to
            phase : str, default complex
                if phase == vacuum, then the complex will not be solvated with water; else, it will be solvated with tip3p
            conduct_endstate_validation : bool, default True
                whether to conduct an endstate validation of the hybrid topology factory
            ligand_filename : str, default None
                path to ligand of interest (i.e. small molecule or protein); .sdf or .pdb
            ligand_index : int, default 0
                which ligand to use
            forcefield_files : list of str, default ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
                forcefield files for proteins and solvent
            barostat : openmm.MonteCarloBarostat, default openmm.MonteCarloBarostat(1.0 * unit.atmosphere, 300 * unit.kelvin, 50)
                barostat to use
            forcefield_kwargs : dict, default {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
                forcefield kwargs for system parametrization
            periodic_forcefield_kwargs : dict, default {'nonbondedMethod': app.PME}
                periodic forcefield kwargs for system parametrization
            nonperiodic_forcefield_kwargs : dict, default None
                non-periodic forcefield kwargs for system parametrization
            small_molecule_forcefields : str, default 'gaff-2.11'
                the forcefield string for small molecule parametrization

        TODO : allow argument for spectator ligands besides the 'ligand_filename'

        """

        # First thing to do is load the apo protein to mutate...
        protein_pdbfile = open(protein_filename, 'r')
        protein_pdb = app.PDBFile(protein_pdbfile)
        protein_pdbfile.close()
        protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
        protein_topology = protein_md_topology.to_openmm()
        protein_n_atoms = protein_md_topology.n_atoms

        # Load the ligand, if present
        molecules = []
        if ligand_filename:
            if ligand_filename.endswith('.sdf'): # small molecule
                ligand_mol = createOEMolFromSDF(ligand_filename, index=ligand_index)
                ligand_mol = generate_unique_atom_names(ligand_mol)
                molecules.append(Molecule.from_openeye(ligand_mol, allow_undefined_stereo=False))
                ligand_positions, ligand_topology = extractPositionsFromOEMol(ligand_mol),  forcefield_generators.generateTopologyFromOEMol(ligand_mol)
                ligand_md_topology = md.Topology.from_openmm(ligand_topology)
                ligand_n_atoms = ligand_md_topology.n_atoms

            elif ligand_filename.endswith('pdb'): # protein
                ligand_pdbfile = open(ligand_filename, 'r')
                ligand_pdb = app.PDBFile(ligand_pdbfile)
                ligand_pdbfile.close()
                ligand_positions, ligand_topology, ligand_md_topology = ligand_pdb.positions, ligand_pdb.topology, md.Topology.from_openmm(
                    ligand_pdb.topology)
                ligand_n_atoms = ligand_md_topology.n_atoms

            # Now create a complex
            complex_md_topology = protein_md_topology.join(ligand_md_topology)
            complex_topology = complex_md_topology.to_openmm()
            complex_positions = unit.Quantity(np.zeros([protein_n_atoms + ligand_n_atoms, 3]), unit=unit.nanometers)
            complex_positions[:protein_n_atoms, :] = protein_positions
            complex_positions[protein_n_atoms:, :] = ligand_positions

        # Now for a system_generator
        self.system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                                nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                small_molecule_forcefield=small_molecule_forcefields,
                                                molecules=molecules,
                                                cache=None)

        # Solvate apo and complex...
        apo_input = list(self._solvate(protein_topology, protein_positions, 'tip3p', phase=phase))
        inputs = [apo_input]
        if ligand_filename:
            inputs.append(self._solvate(complex_topology, complex_positions, 'tip3p', phase=phase))

        geometry_engine = FFAllAngleGeometryEngine(metadata=None,
                                                use_sterics=False,
                                                n_bond_divisions=100,
                                                n_angle_divisions=180,
                                                n_torsion_divisions=360,
                                                verbose=True,
                                                storage=None,
                                                bond_softening_constant=1.0,
                                                angle_softening_constant=1.0,
                                                neglect_angles = False,
                                                use_14_nonbondeds = True)


        # Run pipeline...
        htfs = []
        for (top, pos, sys) in inputs:
            point_mutation_engine = PointMutationEngine(wildtype_topology=top,
                                                                 system_generator=self.system_generator,
                                                                 chain_id=mutation_chain_id, # Denote the chain id allowed to mutate (it's always a string variable)
                                                                 max_point_mutants=1,
                                                                 residues_allowed_to_mutate=[mutation_residue_id], # The residue ids allowed to mutate
                                                                 allowed_mutations=[(mutation_residue_id, proposed_residue)], # The residue ids allowed to mutate with the three-letter code allowed to change
                                                                 aggregate=True) # Always allow aggregation

            topology_proposal = point_mutation_engine.propose(sys, top)

            # Edit map
            del topology_proposal.new_to_old_atom_map[10]
            
            print(topology_proposal.new_to_old_atom_map)
            
            new_positions, logp_proposal = geometry_engine.propose(topology_proposal, pos, beta)
            logp_reverse = geometry_engine.logp_reverse(topology_proposal, new_positions, pos, beta)

            forward_htf = HybridTopologyFactory(topology_proposal=topology_proposal,
                                                 current_positions=pos,
                                                 new_positions=new_positions,
                                                 use_dispersion_correction=False,
                                                 functions=None,
                                                 softcore_alpha=None,
                                                 bond_softening_constant=1.0,
                                                 angle_softening_constant=1.0,
                                                 soften_only_new=False,
                                                 neglected_new_angle_terms=[],
                                                 neglected_old_angle_terms=[],
                                                 softcore_LJ_v2=True,
                                                 softcore_electrostatics=True,
                                                 softcore_LJ_v2_alpha=0.85,
                                                 softcore_electrostatics_alpha=0.3,
                                                 softcore_sigma_Q=1.0,
                                                 interpolate_old_and_new_14s=False,
                                                 omitted_terms=None)

            if not topology_proposal.unique_new_atoms:
                assert geometry_engine.forward_final_context_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.forward_final_context_reduced_potential})"
                assert geometry_engine.forward_atoms_with_positions_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's forward atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.forward_atoms_with_positions_reduced_potential})"
                vacuum_added_valence_energy = 0.0
            else:
                added_valence_energy = geometry_engine.forward_final_context_reduced_potential - geometry_engine.forward_atoms_with_positions_reduced_potential

            if not topology_proposal.unique_old_atoms:
                assert geometry_engine.reverse_final_context_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.reverse_final_context_reduced_potential})"
                assert geometry_engine.reverse_atoms_with_positions_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.reverse_atoms_with_positions_reduced_potential})"
                subtracted_valence_energy = 0.0
            else:
                subtracted_valence_energy = geometry_engine.reverse_final_context_reduced_potential - geometry_engine.reverse_atoms_with_positions_reduced_potential


            if conduct_endstate_validation:
                zero_state_error, one_state_error = validate_endstate_energies(forward_htf._topology_proposal, forward_htf, added_valence_energy, subtracted_valence_energy, beta=beta, ENERGY_THRESHOLD=ENERGY_THRESHOLD)
                assert zero_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 0 state is above the threshold ({ENERGY_THRESHOLD}): {zero_state_error}"
                assert one_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 1 state is above the threshold ({ENERGY_THRESHOLD}): {one_state_error}"
            else:
                pass

            htfs.append(forward_htf)

        self.apo_htf = htfs[0]
        self.complex_htf = htfs[1] if ligand_filename else None

    def get_complex_htf(self):
        return self.complex_htf

    def get_apo_htf(self):
        return self.apo_htf


    def _solvate(self,
                        topology,
                        positions,
                        model,
                        phase):
        """
        Generate a solvated topology, positions, and system for a given input topology and positions.
        For generating the system, the forcefield files provided in the constructor will be used.

        Parameters
        ----------
        topology : app.Topology
            Topology of the system to solvate
        positions : [n, 3] ndarray of Quantity nm
            the positions of the unsolvated system
        forcefield : SystemGenerator.forcefield
            forcefield file of solvent to add
        model : str, default 'tip3p'
            solvent model to use for solvation

        Returns
        -------
        solvated_topology : app.Topology
            Topology of the system with added waters
        solvated_positions : [n + 3(n_waters), 3] ndarray of Quantity nm
            Solvated positions
        solvated_system : openmm.System
            The parameterized system, containing a barostat if one was specified.
        """
        modeller = app.Modeller(topology, positions)


        # Now we have to add missing atoms
        if phase != 'vacuum':
            modeller.addSolvent(self.system_generator.forcefield, model=model, padding=1.0 * unit.nanometers, ionicStrength=0.15*unit.molar)
        else:
            pass

        solvated_topology = modeller.getTopology()
        solvated_positions = modeller.getPositions()

        # Canonicalize the solvated positions: turn tuples into np.array
        solvated_positions = unit.quantity.Quantity(value=np.array([list(atom_pos) for atom_pos in solvated_positions.value_in_unit_system(unit.md_unit_system)]), unit=unit.nanometers)
        solvated_system = self.system_generator.create_system(solvated_topology)

        return solvated_topology, solvated_positions, solvated_system


In [13]:
# Solvent
import pickle
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/4/"

# Create hybrid topology factory
apo_delivery = PointMutationExecutor(f"../input/ala_vacuum.pdb", 
                        '1', 
                        '2', 
                        'THR',
                       )
pickle.dump(apo_delivery.get_apo_htf(), open(os.path.join(output_dir, "2_5/2_5_solvent.pickle"), "wb" ))


DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load gaff-2.11
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:[4, 4, 4, 4, 4, 4]
INFO:proposal_generator:Maximum atom matched after hydrogen exceptions: 2
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...


{6: 6, 8: 8, 11: 13, 12: 14, 7: 7, 9: 9, 0: 0, 1: 1, 2: 2, 3: 3, 4: 4, 5: 5, 20: 16, 21: 17, 22: 18, 23: 19, 24: 20, 25: 21, 26: 22, 27: 23, 28: 24, 29: 25, 30: 26, 31: 27, 32: 28, 33: 29, 34: 30, 35: 31, 36: 32, 37: 33, 38: 34, 39: 35, 40: 36, 41: 37, 42: 38, 43: 39, 44: 40, 45: 41, 46: 42, 47: 43, 48: 44, 49: 45, 50: 46, 51: 47, 52: 48, 53: 49, 54: 50, 55: 51, 56: 52, 57: 53, 58: 54, 59: 55, 60: 56, 61: 57, 62: 58, 63: 59, 64: 60, 65: 61, 66: 62, 67: 63, 68: 64, 69: 65, 70: 66, 71: 67, 72: 68, 73: 69, 74: 70, 75: 71, 76: 72, 77: 73, 78: 74, 79: 75, 80: 76, 81: 77, 82: 78, 83: 79, 84: 80, 85: 81, 86: 82, 87: 83, 88: 84, 89: 85, 90: 86, 91: 87, 92: 88, 93: 89, 94: 90, 95: 91, 96: 92, 97: 93, 98: 94, 99: 95, 100: 96, 101: 97, 102: 98, 103: 99, 104: 100, 105: 101, 106: 102, 107: 103, 108: 104, 109: 105, 110: 106, 111: 107, 112: 108, 113: 109, 114: 110, 115: 111, 116: 112, 117: 113, 118: 114, 119: 115, 120: 116, 121: 117, 122: 118, 123: 119, 124: 120, 125: 121, 126: 122, 127: 123, 128: 12

AssertionError: There is a connectivity issue; there are no torsions from which to choose

In [ ]:
# Vacuum
import pickle
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/4/"

# Create hybrid topology factory
apo_delivery = PointMutationExecutor(f"../input/ala_vacuum.pdb", 
                              '1', 
                              '2', 
                              'THR',
                              phase='vacuum',
	                          barostat=None,
	                          periodic_forcefield_kwargs=None, 
	                          nonperiodic_forcefield_kwargs={'nonbondedMethod': app.NoCutoff}
                             )
pickle.dump(apo_delivery.get_apo_htf(), open(os.path.join(output_dir, "2_5/2_5_vacuum.pickle"), "wb" ))





In [2]:
# Read in htf
import pickle
with open("/data/chodera/zhangi/perses_benchmark/neq/3/2/2_vacuum.pickle", 'rb') as f:
    htf = pickle.load(f)

In [5]:
for key, val in htf._topology_proposal.new_to_old_atom_map.items():
    print(type(key))

<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>
<class 'int'>


In [3]:
for atom in htf._topology_proposal.old_topology.atoms():
    print(atom)

<Atom 0 (H1) of chain 0 residue 0 (ACE)>
<Atom 1 (CH3) of chain 0 residue 0 (ACE)>
<Atom 2 (H2) of chain 0 residue 0 (ACE)>
<Atom 3 (H3) of chain 0 residue 0 (ACE)>
<Atom 4 (C) of chain 0 residue 0 (ACE)>
<Atom 5 (O) of chain 0 residue 0 (ACE)>
<Atom 6 (N) of chain 0 residue 1 (ALA)>
<Atom 7 (H) of chain 0 residue 1 (ALA)>
<Atom 8 (CA) of chain 0 residue 1 (ALA)>
<Atom 9 (HA) of chain 0 residue 1 (ALA)>
<Atom 10 (CB) of chain 0 residue 1 (ALA)>
<Atom 11 (HB2) of chain 0 residue 1 (ALA)>
<Atom 12 (HB3) of chain 0 residue 1 (ALA)>
<Atom 13 (C) of chain 0 residue 1 (ALA)>
<Atom 14 (O) of chain 0 residue 1 (ALA)>
<Atom 15 (HB1) of chain 0 residue 1 (ALA)>
<Atom 16 (N) of chain 0 residue 2 (NME)>
<Atom 17 (H) of chain 0 residue 2 (NME)>
<Atom 18 (C) of chain 0 residue 2 (NME)>
<Atom 19 (H1) of chain 0 residue 2 (NME)>
<Atom 20 (H2) of chain 0 residue 2 (NME)>
<Atom 21 (H3) of chain 0 residue 2 (NME)>


In [3]:
for atom in htf._topology_proposal.new_topology.atoms():
    print(atom)

<Atom 0 (H1) of chain 0 residue 0 (ACE)>
<Atom 1 (CH3) of chain 0 residue 0 (ACE)>
<Atom 2 (H2) of chain 0 residue 0 (ACE)>
<Atom 3 (H3) of chain 0 residue 0 (ACE)>
<Atom 4 (C) of chain 0 residue 0 (ACE)>
<Atom 5 (O) of chain 0 residue 0 (ACE)>
<Atom 6 (N) of chain 0 residue 1 (THR)>
<Atom 7 (H) of chain 0 residue 1 (THR)>
<Atom 8 (CA) of chain 0 residue 1 (THR)>
<Atom 9 (HA) of chain 0 residue 1 (THR)>
<Atom 10 (CB) of chain 0 residue 1 (THR)>
<Atom 11 (C) of chain 0 residue 1 (THR)>
<Atom 12 (O) of chain 0 residue 1 (THR)>
<Atom 13 (HB) of chain 0 residue 1 (THR)>
<Atom 14 (CG2) of chain 0 residue 1 (THR)>
<Atom 15 (HG21) of chain 0 residue 1 (THR)>
<Atom 16 (HG22) of chain 0 residue 1 (THR)>
<Atom 17 (HG23) of chain 0 residue 1 (THR)>
<Atom 18 (OG1) of chain 0 residue 1 (THR)>
<Atom 19 (HG1) of chain 0 residue 1 (THR)>
<Atom 20 (N) of chain 0 residue 2 (NME)>
<Atom 21 (H) of chain 0 residue 2 (NME)>
<Atom 22 (C) of chain 0 residue 2 (NME)>
<Atom 23 (H1) of chain 0 residue 2 (NME)>
<

## Set sigma and epsilon for LJ of OH to 0.1

#### vacuum

In [2]:
# Create system generator
forcefield_files = ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
barostat = None
forcefield_kwargs = {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
periodic_forcefield_kwargs = None
nonperiodic_forcefield_kwargs={'nonbondedMethod': app.NoCutoff}
system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                                nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                cache=None)

RDKit WARNING: [22:10:35] Enabling RDKit 2019.09.3 jupyter extensions


In [3]:
# Generate old system in vacuum

# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/ala_vacuum.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

old_system = system_generator.create_system(protein_topology)

In [4]:
# Generate new apo system in vacuum

# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/thr_vacuum.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

new_system = system_generator.create_system(protein_topology)

In [5]:
for atom in protein_topology.atoms():
    print(atom, atom.index)

<Atom 0 (H1) of chain 0 residue 0 (ACE)> 0
<Atom 1 (CH3) of chain 0 residue 0 (ACE)> 1
<Atom 2 (H2) of chain 0 residue 0 (ACE)> 2
<Atom 3 (H3) of chain 0 residue 0 (ACE)> 3
<Atom 4 (C) of chain 0 residue 0 (ACE)> 4
<Atom 5 (O) of chain 0 residue 0 (ACE)> 5
<Atom 6 (N) of chain 0 residue 1 (THR)> 6
<Atom 7 (H) of chain 0 residue 1 (THR)> 7
<Atom 8 (CA) of chain 0 residue 1 (THR)> 8
<Atom 9 (HA) of chain 0 residue 1 (THR)> 9
<Atom 10 (CB) of chain 0 residue 1 (THR)> 10
<Atom 11 (C) of chain 0 residue 1 (THR)> 11
<Atom 12 (O) of chain 0 residue 1 (THR)> 12
<Atom 13 (HB) of chain 0 residue 1 (THR)> 13
<Atom 14 (CG2) of chain 0 residue 1 (THR)> 14
<Atom 15 (HG21) of chain 0 residue 1 (THR)> 15
<Atom 16 (HG22) of chain 0 residue 1 (THR)> 16
<Atom 17 (HG23) of chain 0 residue 1 (THR)> 17
<Atom 18 (OG1) of chain 0 residue 1 (THR)> 18
<Atom 19 (HG1) of chain 0 residue 1 (THR)> 19
<Atom 20 (N) of chain 0 residue 2 (NME)> 20
<Atom 21 (H) of chain 0 residue 2 (NME)> 21
<Atom 22 (C) of chain 0 resi

In [6]:
for i in range(new_system.getNumForces()):
    print(i, new_system.getForce(i))

0 <simtk.openmm.openmm.HarmonicBondForce; proxy of <Swig Object of type 'OpenMM::HarmonicBondForce *' at 0x2b414a035180> >
1 <simtk.openmm.openmm.HarmonicAngleForce; proxy of <Swig Object of type 'OpenMM::HarmonicAngleForce *' at 0x2b414a035180> >
2 <simtk.openmm.openmm.PeriodicTorsionForce; proxy of <Swig Object of type 'OpenMM::PeriodicTorsionForce *' at 0x2b414a035180> >
3 <simtk.openmm.openmm.NonbondedForce; proxy of <Swig Object of type 'OpenMM::NonbondedForce *' at 0x2b414a035180> >


In [7]:
nonbonded_force = new_system.getForces()[3]

In [8]:
for idx in range(nonbonded_force.getNumParticles()):
    parameters = nonbonded_force.getParticleParameters(idx)
    print(idx, parameters)

0 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
1 [Quantity(value=-0.3662, unit=elementary charge), Quantity(value=0.3399669508423535, unit=nanometer), Quantity(value=0.4577296, unit=kilojoule/mole)]
2 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
3 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
4 [Quantity(value=0.5972, unit=elementary charge), Quantity(value=0.3399669508423535, unit=nanometer), Quantity(value=0.359824, unit=kilojoule/mole)]
5 [Quantity(value=-0.5679, unit=elementary charge), Quantity(value=0.2959921901149463, unit=nanometer), Quantity(value=0.87864, unit=kilojoule/mole)]
6 [Quantity(value=-0.4157, unit=elementary charge), Quantity(valu

In [9]:
new_system.getForce(3).setParticleParameters(19, 0.4102, 1.0, 0.1)

In [10]:
new_system.getForce(3).getParticleParameters(19)

[Quantity(value=0.4102, unit=elementary charge),
 Quantity(value=1.0, unit=nanometer),
 Quantity(value=0.1, unit=kilojoule/mole)]

In [1]:
from simtk.openmm import unit, app
from openmmforcefields.generators import SystemGenerator
import mdtraj as md
import numpy as np

In [2]:
# Create system generator
forcefield_files = ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
barostat = None
forcefield_kwargs = {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
periodic_forcefield_kwargs = None
nonperiodic_forcefield_kwargs={'nonbondedMethod': app.NoCutoff}
system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                                nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                cache=None)

RDKit WARNING: [22:10:35] Enabling RDKit 2019.09.3 jupyter extensions


In [3]:
# Generate old system in vacuum

# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/ala_vacuum.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

old_system = system_generator.create_system(protein_topology)

In [4]:
# Generate new apo system in vacuum

# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/thr_vacuum.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

new_system = system_generator.create_system(protein_topology)

In [5]:
for atom in protein_topology.atoms():
    print(atom, atom.index)

<Atom 0 (H1) of chain 0 residue 0 (ACE)> 0
<Atom 1 (CH3) of chain 0 residue 0 (ACE)> 1
<Atom 2 (H2) of chain 0 residue 0 (ACE)> 2
<Atom 3 (H3) of chain 0 residue 0 (ACE)> 3
<Atom 4 (C) of chain 0 residue 0 (ACE)> 4
<Atom 5 (O) of chain 0 residue 0 (ACE)> 5
<Atom 6 (N) of chain 0 residue 1 (THR)> 6
<Atom 7 (H) of chain 0 residue 1 (THR)> 7
<Atom 8 (CA) of chain 0 residue 1 (THR)> 8
<Atom 9 (HA) of chain 0 residue 1 (THR)> 9
<Atom 10 (CB) of chain 0 residue 1 (THR)> 10
<Atom 11 (C) of chain 0 residue 1 (THR)> 11
<Atom 12 (O) of chain 0 residue 1 (THR)> 12
<Atom 13 (HB) of chain 0 residue 1 (THR)> 13
<Atom 14 (CG2) of chain 0 residue 1 (THR)> 14
<Atom 15 (HG21) of chain 0 residue 1 (THR)> 15
<Atom 16 (HG22) of chain 0 residue 1 (THR)> 16
<Atom 17 (HG23) of chain 0 residue 1 (THR)> 17
<Atom 18 (OG1) of chain 0 residue 1 (THR)> 18
<Atom 19 (HG1) of chain 0 residue 1 (THR)> 19
<Atom 20 (N) of chain 0 residue 2 (NME)> 20
<Atom 21 (H) of chain 0 residue 2 (NME)> 21
<Atom 22 (C) of chain 0 resi

In [6]:
for i in range(new_system.getNumForces()):
    print(i, new_system.getForce(i))

0 <simtk.openmm.openmm.HarmonicBondForce; proxy of <Swig Object of type 'OpenMM::HarmonicBondForce *' at 0x2b414a035180> >
1 <simtk.openmm.openmm.HarmonicAngleForce; proxy of <Swig Object of type 'OpenMM::HarmonicAngleForce *' at 0x2b414a035180> >
2 <simtk.openmm.openmm.PeriodicTorsionForce; proxy of <Swig Object of type 'OpenMM::PeriodicTorsionForce *' at 0x2b414a035180> >
3 <simtk.openmm.openmm.NonbondedForce; proxy of <Swig Object of type 'OpenMM::NonbondedForce *' at 0x2b414a035180> >


In [7]:
nonbonded_force = new_system.getForces()[3]

In [8]:
for idx in range(nonbonded_force.getNumParticles()):
    parameters = nonbonded_force.getParticleParameters(idx)
    print(idx, parameters)

0 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
1 [Quantity(value=-0.3662, unit=elementary charge), Quantity(value=0.3399669508423535, unit=nanometer), Quantity(value=0.4577296, unit=kilojoule/mole)]
2 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
3 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
4 [Quantity(value=0.5972, unit=elementary charge), Quantity(value=0.3399669508423535, unit=nanometer), Quantity(value=0.359824, unit=kilojoule/mole)]
5 [Quantity(value=-0.5679, unit=elementary charge), Quantity(value=0.2959921901149463, unit=nanometer), Quantity(value=0.87864, unit=kilojoule/mole)]
6 [Quantity(value=-0.4157, unit=elementary charge), Quantity(valu

In [9]:
new_system.getForce(3).setParticleParameters(19, 0.4102, 1.0, 0.1)

In [10]:
new_system.getForce(3).getParticleParameters(19)

[Quantity(value=0.4102, unit=elementary charge),
 Quantity(value=1.0, unit=nanometer),
 Quantity(value=0.1, unit=kilojoule/mole)]

In [12]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [14]:
# Generate vacuum htf 
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
from simtk.openmm import app
vacuum_delivery = PointMutationExecutor("../input/ala_vacuum.pdb", 
                        '1', # First chain is the barstar one
                        '2', 
                        'THR',
                        phase='vacuum',
                        barostat=None,
                        periodic_forcefield_kwargs=None,
                        nonperiodic_forcefield_kwargs={'nonbondedMethod': app.NoCutoff},
                        old_system=old_system,
                        new_system=new_system
                       )


DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load gaff-2.11
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:[4, 4, 4, 4, 4, 4]
INFO:proposal_generator:Maximum atom matched after hydrogen exceptions: 2
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...
INFO:geometry:number of atoms to be placed: 7
INFO:geometry:Atom index proposal order is [18, 14, 19, 16, 17, 13, 15]
INFO:geometry:omitted_bonds: []
INFO:geometry:direction of proposal is forward; creating atoms_with_positions and new positions from old system/topology...
INFO:geometry:creating growth system...
INFO:geometry:	creating bond force...
INFO:geometry:	there are 11 bonds in reference force.
INFO:geometry:	creating angle force...
INFO:geometry:	there are 43 angles in refere

conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 7 new atoms
INFO:geometry:	reduced angle potential = 0.15726219829816976.
INFO:geometry:	reduced angle potential = 0.0025389797436132272.
INFO:geometry:	reduced angle potential = 0.00754868459415853.
INFO:geometry:	reduced angle potential = 0.6311852277829375.
INFO:geometry:	reduced angle potential = 0.0064023116935769805.
INFO:geometry:	reduced angle potential = 0.16062153448623837.
INFO:geometry:	reduced angle potential = 0.016656756170311076.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonbonded final system forces ['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce']
INFO:geometry:	final no-nonbonded final system forces dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:geometry:	there are 11 bond forces in the no-nonbonded final system
INFO:geometry:	there are 43 angle forces in the no-nonbonded final system
INFO:geometry:	t

...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: 10.845303282440007
INFO:geometry:final reduced energy 27.664692045560134
INFO:geometry:sum of energies: 27.66469154876837
INFO:geometry:magnitude of difference in the energies: 4.967917632825447e-07
INFO:geometry:Final logp_proposal: 14.132248444188425


added energy components: [('CustomBondForce', 0.0), ('CustomAngleForce', 1.5196358350712886), ('CustomTorsionForce', 0.005213740573906639), ('CustomBondForce', 9.320453706794812)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 0
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:No MonteCarloBarostat added.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=2.0, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=2.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=2.0), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions dict...
INFO:relative:Generating new system except

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 0.0333668919871159
			HarmonicAngleForce: 2.134739442948204
			PeriodicTorsionForce: 16.17613147765423
			NonbondedForce: -38.74516998365842
			AndersenThermostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 0.033366891987115906
			HarmonicBondForce: 0.9217412142107074
			CustomAngleForce: 0.6151036078769154
			HarmonicAngleForce: 8.64670474206453
			CustomTorsionForce: 0.0
			PeriodicTorsionForce: 26.494627120218425
			NonbondedForce: -133.87110719967842
			CustomNonbondedForce: 4.704582417313629
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 0.033366891987115906
			HarmonicBondForce: 0.9217412142107074
			CustomAngleForce: 0.6151036078769154
			HarmonicAngleForce: 8.64670474206453
			CustomTorsionForce: 0.0
			Periodic

In [15]:
output_dir = "/data/chodera/zhangi/perses_benchmark/neq/7/"

In [21]:
import pickle
import os
pickle.dump(vacuum_delivery.get_apo_htf(), open(os.path.join(output_dir, "3/3_vacuum.pickle"), "wb" ))


#### solvent 

In [44]:
from simtk import openmm 
# Create system generator
forcefield_files = ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
barostat = openmm.MonteCarloBarostat(1.0 * unit.atmosphere, 300 * unit.kelvin, 50)
forcefield_kwargs = {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
periodic_forcefield_kwargs = {'nonbondedMethod': app.PME}
nonperiodic_forcefield_kwargs = None
system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                                nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                cache=None)

DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load openff-1.0.0
DEBUG:perses.forcefields.system_generators:  GAFFTemplateGenerator cannot load openff-1.0.0
DEBUG:perses.forcefields.system_generators:Specified 'forcefield' (openff-1.0.0) must be one of ['gaff-1.4', 'gaff-1.8', 'gaff-1.81', 'gaff-2.1', 'gaff-2.11']
DEBUG:perses.forcefields.system_generators:Trying SMIRNOFFTemplateGenerator to load openff-1.0.0


In [45]:
# Generate old system in vacuum

# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/ala_vacuum.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

old_system = system_generator.create_system(protein_topology)

In [46]:
# Generate new apo system in vacuum

# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/thr_vacuum.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

new_system = system_generator.create_system(protein_topology)

In [47]:
for atom in protein_topology.atoms():
    print(atom, atom.index)

<Atom 0 (H1) of chain 0 residue 0 (ACE)> 0
<Atom 1 (CH3) of chain 0 residue 0 (ACE)> 1
<Atom 2 (H2) of chain 0 residue 0 (ACE)> 2
<Atom 3 (H3) of chain 0 residue 0 (ACE)> 3
<Atom 4 (C) of chain 0 residue 0 (ACE)> 4
<Atom 5 (O) of chain 0 residue 0 (ACE)> 5
<Atom 6 (N) of chain 0 residue 1 (THR)> 6
<Atom 7 (H) of chain 0 residue 1 (THR)> 7
<Atom 8 (CA) of chain 0 residue 1 (THR)> 8
<Atom 9 (HA) of chain 0 residue 1 (THR)> 9
<Atom 10 (CB) of chain 0 residue 1 (THR)> 10
<Atom 11 (C) of chain 0 residue 1 (THR)> 11
<Atom 12 (O) of chain 0 residue 1 (THR)> 12
<Atom 13 (HB) of chain 0 residue 1 (THR)> 13
<Atom 14 (CG2) of chain 0 residue 1 (THR)> 14
<Atom 15 (HG21) of chain 0 residue 1 (THR)> 15
<Atom 16 (HG22) of chain 0 residue 1 (THR)> 16
<Atom 17 (HG23) of chain 0 residue 1 (THR)> 17
<Atom 18 (OG1) of chain 0 residue 1 (THR)> 18
<Atom 19 (HG1) of chain 0 residue 1 (THR)> 19
<Atom 20 (N) of chain 0 residue 2 (NME)> 20
<Atom 21 (H) of chain 0 residue 2 (NME)> 21
<Atom 22 (C) of chain 0 resi

In [48]:
for i in range(new_system.getNumForces()):
    print(i, new_system.getForce(i))

0 <simtk.openmm.openmm.HarmonicBondForce; proxy of <Swig Object of type 'OpenMM::HarmonicBondForce *' at 0x2b4153d1c030> >
1 <simtk.openmm.openmm.HarmonicAngleForce; proxy of <Swig Object of type 'OpenMM::HarmonicAngleForce *' at 0x2b4153d1c030> >
2 <simtk.openmm.openmm.PeriodicTorsionForce; proxy of <Swig Object of type 'OpenMM::PeriodicTorsionForce *' at 0x2b4153d1c030> >
3 <simtk.openmm.openmm.NonbondedForce; proxy of <Swig Object of type 'OpenMM::NonbondedForce *' at 0x2b4153d1c030> >
4 <simtk.openmm.openmm.MonteCarloBarostat; proxy of <Swig Object of type 'OpenMM::MonteCarloBarostat *' at 0x2b4153d1c030> >


In [49]:
nonbonded_force = new_system.getForces()[3]

In [50]:
for idx in range(nonbonded_force.getNumParticles()):
    parameters = nonbonded_force.getParticleParameters(idx)
    print(idx, parameters)

0 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
1 [Quantity(value=-0.3662, unit=elementary charge), Quantity(value=0.3399669508423535, unit=nanometer), Quantity(value=0.4577296, unit=kilojoule/mole)]
2 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
3 [Quantity(value=0.1123, unit=elementary charge), Quantity(value=0.2649532787749369, unit=nanometer), Quantity(value=0.06568879999999999, unit=kilojoule/mole)]
4 [Quantity(value=0.5972, unit=elementary charge), Quantity(value=0.3399669508423535, unit=nanometer), Quantity(value=0.359824, unit=kilojoule/mole)]
5 [Quantity(value=-0.5679, unit=elementary charge), Quantity(value=0.2959921901149463, unit=nanometer), Quantity(value=0.87864, unit=kilojoule/mole)]
6 [Quantity(value=-0.4157, unit=elementary charge), Quantity(valu

In [51]:
new_system.getForce(3).setParticleParameters(19, 0.4102, 1.0, 0.1)

In [52]:
new_system.getForce(3).getParticleParameters(19)

[Quantity(value=0.4102, unit=elementary charge),
 Quantity(value=1.0, unit=nanometer),
 Quantity(value=0.1, unit=kilojoule/mole)]

In [53]:
# Generate solvent htf 
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
from simtk.openmm import app
solvent_delivery = PointMutationExecutor("../input/ala_vacuum.pdb", 
                        '1', 
                        '2', 
                        'THR',
                        old_system=old_system,
                        new_system=new_system
                       )


DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load gaff-2.11
INFO:root:solvating at 0.15 M using tip3p
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:[4, 4, 4, 4, 4, 4]
INFO:proposal_generator:Maximum atom matched after hydrogen exceptions: 2
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...
INFO:geometry:number of atoms to be placed: 7
INFO:geometry:Atom index proposal order is [14, 18, 13, 15, 19, 16, 17]
INFO:geometry:omitted_bonds: []
INFO:geometry:direction of proposal is forward; creating atoms_with_positions and new positions from old system/topology...
INFO:geometry:creating growth system...
INFO:geometry:	creating bond force...
INFO:geometry:	there are 11 bonds in reference force.
INFO:geometry:	creating angle force...
IN

conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 7 new atoms
INFO:geometry:	reduced angle potential = 0.0001910913178359153.
INFO:geometry:	reduced angle potential = 0.02630899298632865.
INFO:geometry:	reduced angle potential = 0.040250088176231893.
INFO:geometry:	reduced angle potential = 0.5810204668451804.
INFO:geometry:	reduced angle potential = 0.2768817817460261.
INFO:geometry:	reduced angle potential = 0.4208216896781388.
INFO:geometry:	reduced angle potential = 0.4539319175873373.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonbonded final system forces ['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat']
INFO:geometry:	final no-nonbonded final system forces dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:geometry:	there are 11 bond forces in the no-nonbonded final system
INFO:geometry:	there are 43 angle forces in the no-nonbonded final system

...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: 10.845303282440007
INFO:geometry:final reduced energy 27.664692045560198
INFO:geometry:sum of energies: 27.66469154876837
INFO:geometry:magnitude of difference in the energies: 4.967918272313909e-07
INFO:geometry:Final logp_proposal: 13.472257140146416


added energy components: [('CustomBondForce', 0.0), ('CustomAngleForce', 1.5196358350712886), ('CustomTorsionForce', 0.005213740573906639), ('CustomBondForce', 9.320453706794812)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 0
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=2.0, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=2.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=2.0), unit=nanometer)]


KeyError: 26

In [ ]:
import pickle
import os
pickle.dump(solvent_delivery.get_apo_htf(), open(os.path.join(output_dir, "3/3_solvent.pickle"), "wb" ))


In [14]:
# Check if the positions are nan after adding LJ padding
import numpy as np
with open("/data/chodera/zhangi/perses_benchmark/neq/7/3/3_vacuum_0_forward.npy", 'rb') as f:
    pos = np.load(f)

In [15]:
pos.shape

(10, 20001)

In [16]:
for val in np.ndarray.flatten(pos):
    print(val)

0.0
-0.0002753060310986017
-0.0005652055678546996
-0.0008531669649777472
-0.0011295062967948322
-0.0013895484226707996
-0.001637635952345862
-0.0018992630177951872
-0.0021818890228687687
-0.002480058345378708
-0.0027885525651606164
-0.0030881187690353354
-0.0033873828275757566
-0.0036494053299564086
-0.0038648784967230537
-0.004045606526531968
-0.004229362780696448
-0.0044470049963881535
-0.0047153223049030005
-0.005026573105662509
-0.005345744328711671
-0.005645304288870243
-0.005922334127834118
-0.006173212959514368
-0.006400587163224609
-0.006627717421899332
-0.006865748865090895
-0.007111261339591494
-0.007366718929291434
-0.0076389499935702945
-0.00792888719218332
-0.008229617750578316
-0.00852073552614125
-0.008774760800173937
-0.009018673033467314
-0.009258954024265912
-0.009492279577150911
-0.009729340349038516
-0.009974101601593378
-0.010251042919703681
-0.010549151125530086
-0.010870677912021814
-0.011205968233069056
-0.011538215560952306
-0.01184544297793435
-0.0121248174721

2.539770125092101
2.5415500767778263
2.543276815616971
2.544976494793545
2.5466814937521383
2.5483948987255998
2.55012582358123
2.5518759660806887
2.553674979282043
2.555523704093357
2.557438739150268
2.559399844659204
2.5614020432706575
2.563415158487296
2.565450739913768
2.567543753500984
2.56970092122177
2.5719277512209886
2.574202991363441
2.576542379190774
2.578977670659637
2.581481758744062
2.584050845182151
2.5866669887204394
2.5893333286114064
2.592049777719911
2.594810342466813
2.5976214039987253
2.600468788772687
2.6033233245860767
2.6061997199772273
2.6091116251882185
2.612081063025618
2.6151141805891
2.618231389305483
2.621429719858022
2.624706166050236
2.6280418040059166
2.6314339958377144
2.634885865971406
2.6383897255123454
2.6419419943390436
2.645561938184471
2.649258907470691
2.6530459021542483
2.6568815112952877
2.6607512359368157
2.664658531110116
2.6686142375249258
2.672612756076369
2.676632618360257
2.6806523015050443
2.684656779139833
2.6886243530612313
2.69253974

18.406369297852198
18.417614057243924
18.428858587900955
18.440102428178093
18.451352520918757
18.462666453425204
18.4740714398173
18.485560918696372
18.497118959300863
18.508785798834072
18.52068332451746
18.532705471179597
18.54459718052005
18.556240438672205
18.567610983518787
18.578810417672802
18.5897718006547
18.60051950735308
18.611123811678684
18.62155402552925
18.631943527440132
18.642321245784583
18.652688096394115
18.66305240138602
18.67338286489539
18.683589799304425
18.69369101565542
18.70372136232522
18.71371315343752
18.723682141704252
18.73374491684748
18.743949328391366
18.754346887271463
18.765016334253804
18.775982519997047
18.787255397940417
18.79891001641817
18.81109659179015
18.823842812853876
18.83708670155055
18.850897196777638
18.865052066249085
18.8793416223407
18.893635858595857
18.907740839991067
18.92162346831998
18.935274470029448
18.948581384456322
18.96155984353173
18.974214322153525
18.98655723591853
18.998480190615016
19.009981307653707
19.021103472276

270.6789082077569
270.6895632252892
270.6989020949257
270.70777661857284
270.7170774878016
270.7275365825001
270.7397171031214
270.75257508117164
270.7642845422204
270.77490695690625
270.78505996596914
270.7957240203677
270.80778972436906
270.8208871247361
270.83327780462105
270.8440867798343
270.85392365823105
270.8636487717639
270.87415372378024
270.8857070781568
270.89742910822014
270.9085478706658
270.91879784811044
270.92830704580905
270.9376576917925
270.9476080730793
270.9583007657467
270.9695270349339
270.98086770851825
270.99176876744895
271.0021707800543
271.01267832321815
271.02357332730134
271.03446550678757
271.04498480421245
271.0552419360974
271.065870654895
271.07749355499675
271.08976668781685
271.10158103956485
271.11220821148135
271.1214760619598
271.1300261096569
271.1390220788268
271.1492435118889
271.16099153287803
271.17363474710584
271.1854313825392
271.1957192687576
271.20524867210054
271.21475481916326
271.2248930720352
271.23652407796317
271.2490604093456
271

284.09487719003147
284.0984705648375
284.10205574252393
284.1056274467699
284.10921235913213
284.1128262287927
284.11647098542545
284.12011610057715
284.12374000355436
284.12733111690216
284.13092123731604
284.1345363502231
284.1381768233043
284.1418353106674
284.1455263513958
284.14924012875036
284.1529539415081
284.15664853183534
284.16028839272565
284.1638885971295
284.16744582612097
284.17096848900377
284.17446350918135
284.17796469945193
284.18146161693056
284.1849521594617
284.1884367688217
284.191914028507
284.1953939122572
284.1988802481278
284.2024114451536
284.2059995172332
284.2096301576002
284.21327220023863
284.21689556216023
284.2205215753275
284.2241526423183
284.227784578367
284.23143316968003
284.2351428802014
284.2389247529788
284.242738000362
284.246522645536
284.2502175251734
284.25386489330253
284.2574699630966
284.2610281614589
284.2645268689954
284.2680011292291
284.2714725016711
284.2749486004746
284.2784298704936
284.28191067148487
284.28538297486404
284.288836

...

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


## Analyze

In [11]:
from perses.analysis.analysis import Analysis
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import pymbar
%matplotlib inline
import os
import itertools
from tqdm import tqdm_notebook
import pandas as pd

DEBUG:matplotlib:$HOME=/home/zhangi
DEBUG:matplotlib:CONFIGDIR=/home/zhangi/.config/matplotlib
DEBUG:matplotlib:matplotlib data path: /home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/matplotlib/mpl-data
DEBUG:matplotlib:loaded rc file /home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/matplotlib/mpl-data/matplotlibrc
DEBUG:matplotlib:matplotlib version 3.1.1
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is linux
DEBUG:matplotlib:loaded modules: ['sys', 'builtins', '_frozen_importlib', '_imp', '_thread', '_warnings', '_weakref', 'zipimport', '_frozen_importlib_external', '_io', 'marshal', 'posix', 'encodings', 'codecs', '_codecs', 'encodings.aliases', 'encodings.utf_8', '_signal', '__main__', 'encodings.latin_1', 'io', 'abc', '_abc', '_bootlocale', '_locale', 'site', 'os', 'stat', '_stat', 'posixpath', 'genericpath', 'os.path', '_collections_abc', '_sitebuiltins', 'types', 'importlib', 'importlib._bootstrap', 'importlib._bootstrap_

DEBUG:matplotlib:CACHEDIR=/home/zhangi/.cache/matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from /home/zhangi/.cache/matplotlib/fontlist-v310.json
DEBUG:matplotlib.pyplot:Loaded backend agg version unknown.
DEBUG:matplotlib.pyplot:Loaded backend module://ipykernel.pylab.backend_inline version unknown.
DEBUG:matplotlib.pyplot:Loaded backend module://ipykernel.pylab.backend_inline version unknown.


In [12]:
# Global variables
amino_acids = ['ALA', 'CYS', 'SER', 'THR']

# Create list of tuples for every pair of amino acids
pairs = list(itertools.permutations(amino_acids, r=2))

In [13]:
def analyze(forward_work, reverse_work, forward_accumulated, reverse_accumulated, dir_num, phase, output_dir, title): 
    # Substract offset
    print("subtracting offset")
    forward_work_offset = []
    for cycle in forward_work:
        forward_work_offset.append(np.array([val - cycle[0] for val in cycle[1:]]))
    forward_work_offset = np.array(forward_work_offset)

    reverse_work_offset = []
    for cycle in reverse_work:
        reverse_work_offset.append(np.array([val - cycle[0] for val in cycle[1:]]))
    reverse_work_offset = np.array(reverse_work_offset)
    
    # Compute dg, ddg
    print("computing dg, ddg")
    dg, ddg = pymbar.bar.BAR(forward_accumulated, reverse_accumulated)
    
    # Plot work trajectories
    print("plotting work trajs")
    for cycle in forward_work_offset:
        x = [(i+1)*4e-3 for i in range(len(list(cycle)))]
        y = cycle
        plt.plot(x, y, color=sns.color_palette()[0])
    for cycle in reverse_work_offset:
        x = [(i+1)*4e-3 for i in range(len(list(cycle)))]
        y = -cycle
        plt.plot(x, y, color=sns.color_palette()[1])
    plt.xlabel("$t_{neq}$ (ps)")
    plt.ylabel("work (kT)")
    plt.title(f"{title} {phase}")
    plt.savefig(os.path.join(output_dir, f"{dir_num}_{phase}_work_traj.png"), dpi=500)
    print(f"saved to: {os.path.join(output_dir, f'{dir_num}_{phase}_work_traj.png')}")
    plt.clf()
    
    # Plot work distributions
    print("plotting work distrib")
    accumulated_forward = [cycle[-1] for cycle in forward_work_offset]
    accumulated_reverse = [-cycle[-1] for cycle in reverse_work_offset]
    sns.distplot(accumulated_forward)
    sns.distplot(accumulated_reverse)
    plt.axvline(dg)
    plt.axvline(dg + ddg, linestyle='dashed')
    plt.axvline(dg - ddg, linestyle='dashed')
    plt.xlabel("work (kT)")
    plt.ylabel("p(w)")
    plt.title(f"{title} {phase}")
    plt.savefig(os.path.join(output_dir, f"{dir_num}_{phase}_work_dist.png"), dpi=500)
    print(f"saved to: {os.path.join(output_dir, f'{dir_num}_{phase}_work_dist.png')}")
    plt.clf()
    
    # Compute free energy 
    return dg, ddg
    

In [16]:
# Prep work arrays (from distributed jobs) and call analyze()
d_results = {}
for i in ['2_6']:
    print(f"dir: {i}")
    # Load and combine arrays
    forward_solvent_arrays = []
    reverse_solvent_arrays = []
    forward_vacuum_arrays = []
    reverse_vacuum_arrays = []
    for j in tqdm_notebook(range(100)):
        print(f"job: {j}")
        forward_solvent_path = f'/data/chodera/zhangi/perses_benchmark/neq/4/{i}/{i}_solvent_{j}_forward.npy'
        reverse_solvent_path = f'/data/chodera/zhangi/perses_benchmark/neq/4/{i}/{i}_solvent_{j}_reverse.npy'
        forward_vacuum_path = f'/data/chodera/zhangi/perses_benchmark/neq/4/{i}/{i}_vacuum_{j}_forward.npy'
        reverse_vacuum_path = f'/data/chodera/zhangi/perses_benchmark/neq/4/{i}/{i}_vacuum_{j}_reverse.npy'
        if os.path.exists(forward_solvent_path):
            with open(forward_solvent_path, 'rb') as f:
                forward_solvent_arrays.append(np.load(f))
        if os.path.exists(reverse_solvent_path):
            with open(reverse_solvent_path, 'rb') as f:
                reverse_solvent_arrays.append(np.load(f))
        if os.path.exists(forward_vacuum_path):
            with open(forward_vacuum_path, 'rb') as f:
                forward_vacuum_arrays.append(np.load(f))
        if os.path.exists(reverse_vacuum_path):
            with open(reverse_vacuum_path, 'rb') as f:
                reverse_vacuum_arrays.append(np.load(f))
    
    if forward_solvent_arrays and reverse_solvent_arrays and forward_vacuum_arrays and reverse_vacuum_arrays:
#     if forward_vacuum_arrays and reverse_vacuum_arrays:
        
        forward_solvent_combined = np.concatenate(forward_solvent_arrays)
        print(forward_solvent_combined.shape)
        forward_solvent_accumulated = np.array([cycle[-1] - cycle[0] for cycle in forward_solvent_combined]) # compute this separately bc the last value of the subsampled array is diff than the actual last sample
#         forward_solvent_combined = np.array([cycle[0::100] for cycle in forward_solvent_combined])
        
        reverse_solvent_combined = np.concatenate(reverse_solvent_arrays)
        reverse_solvent_accumulated = np.array([cycle[-1] - cycle[0] for cycle in reverse_solvent_combined])
#         reverse_solvent_combined = np.array([cycle[0::100] for cycle in reverse_solvent_combined])
        
        forward_vacuum_combined = np.concatenate(forward_vacuum_arrays)
        print(forward_vacuum_combined.shape)
        forward_vacuum_accumulated = np.array([cycle[-1] - cycle[0] for cycle in forward_vacuum_combined])
#         forward_vacuum_combined = np.array([cycle[0::100] for cycle in forward_vacuum_combined])
        
        reverse_vacuum_combined = np.concatenate(reverse_vacuum_arrays)
        reverse_vacuum_accumulated = np.array([cycle[-1] - cycle[0] for cycle in reverse_vacuum_combined])
#         reverse_vacuum_combined = np.array([cycle[0::100] for cycle in reverse_vacuum_combined])
    
        
        # Analyze
        solvent_dg, solvent_ddg = analyze(forward_solvent_combined, reverse_solvent_combined, forward_solvent_accumulated, reverse_solvent_accumulated, i, 'solvent', os.path.dirname(forward_solvent_path), f"{pairs[2][0]}->{pairs[2][1]}")
        vacuum_dg, vacuum_ddg = analyze(forward_vacuum_combined, reverse_vacuum_combined, forward_vacuum_accumulated, reverse_vacuum_accumulated, i, 'vacuum', os.path.dirname(forward_vacuum_path), f"{pairs[2][0]}->{pairs[2][1]}")
        solvation_dg = vacuum_dg - solvent_dg
        solvation_ddg = (vacuum_ddg**2 + solvent_ddg**2)**0.5
        d_results[pairs[1]] = [solvation_dg, solvation_ddg]
        print(f"vacuum dg: {vacuum_dg}, solvent_dg: {solvent_dg}")
#         print(vacuum_dg, vacuum_ddg)
    else:
        print(f"dir {i} has at least one phase without data" )

dir: 2_6


/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/ipykernel_launcher.py:10: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  # Remove the CWD from sys.path while we load stuff.


job: 0
job: 1
job: 2
job: 3
job: 4
job: 5
job: 6
job: 7
job: 8
job: 9
job: 10
job: 11
job: 12
job: 13
job: 14
job: 15
job: 16
job: 17
job: 18
job: 19
job: 20
job: 21
job: 22
job: 23
job: 24
job: 25
job: 26
job: 27
job: 28
job: 29
job: 30
job: 31
job: 32
job: 33
job: 34
job: 35
job: 36
job: 37
job: 38
job: 39
job: 40
job: 41
job: 42
job: 43
job: 44
job: 45
job: 46
job: 47
job: 48
job: 49
job: 50
job: 51
job: 52
job: 53
job: 54
job: 55
job: 56
job: 57
job: 58
job: 59
job: 60
job: 61
job: 62
job: 63
job: 64
job: 65
job: 66
job: 67
job: 68
job: 69
job: 70
job: 71
job: 72
job: 73
job: 74
job: 75
job: 76
job: 77
job: 78
job: 79
job: 80
job: 81
job: 82
job: 83
job: 84
job: 85
job: 86
job: 87
job: 88
job: 89
job: 90
job: 91
job: 92
job: 93
job: 94
job: 95
job: 96
job: 97
job: 98
job: 99

(100, 40001)
(100, 40001)
subtracting offset
computing dg, ddg
plotting work trajs
saved to: /data/chodera/zhangi/perses_benchmark/neq/4/2_6/2_6_solvent_work_traj.png
plotting work distrib
saved to: /data/chod

<Figure size 432x288 with 0 Axes>